<a href="https://colab.research.google.com/github/zakstucke/geo-sentiment-analysis/blob/master/FinalVaccineChoropleth.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Data in from Github
https://github.com/zakstucke/geo-sentiment-analysis

In [5]:
import pandas as pd
import plotly.express as px
import datetime

# load in processed data
pd.options.mode.chained_assignment = None  # default='warn' this is needed for false positives warnings on reassigning pd dataframe

# Processed cleaned sentiment source
WHOfile = "https://media.githubusercontent.com/media/zakstucke/geo-sentiment-analysis/master/processed_data/final_csv.txt?token=ARLQAMW5WZTQAMWQY7UIKQTCNVE3M"
WHOdf = pd.read_csv(WHOfile)
# WHOdf.columns
# ['Unnamed: 0', 'text', 'retweet_count', 'like_count', 'created_at', 'lang', 'author_location', 'emotion_1', 'emotion_2', 'emotion_3', 'pos',
#   'neg', 'neu', 'compound', 'cleaned_words', 'iso_code', 'country', 'city', 'lat', 'lng']



# No sentiment, but has cases & vaccines
big_WHO_file = "https://raw.githubusercontent.com/zakstucke/geo-sentiment-analysis/master/data/WHO_covid_data_by_COUNTRY.csv?token=GHSAT0AAAAAABTWTNX7IHEUR6S45X3IWTVOYTNJG5A"
# cols = ["iso_code, date, total_vaccinations,people_vaccinated,people_fully_vaccinated,total_boosters,new_vaccinations,new_vaccinations_smoothed,total_vaccinations_per_hundred,people_vaccinated_per_hundred,\
#  people_fully_vaccinated_per_hundred,total_boosters_per_hundred,new_vaccinations_smoothed_per_million,new_people_vaccinated_smoothed,new_people_vaccinated_smoothed_per_hundred"]
big_WHO_df = pd.read_csv(big_WHO_file)

# Columns
# iso_code,continent,location,date,total_cases,new_cases,new_cases_smoothed,total_deaths,new_deaths,new_deaths_smoothed,total_cases_per_million,new_cases_per_million,new_cases_smoothed_per_million,
# total_deaths_per_million,new_deaths_per_million,new_deaths_smoothed_per_million,reproduction_rate,icu_patients,icu_patients_per_million,hosp_patients,hosp_patients_per_million,weekly_icu_admissions,
# weekly_icu_admissions_per_million,weekly_hosp_admissions,weekly_hosp_admissions_per_million,total_tests,new_tests,total_tests_per_thousand,new_tests_per_thousand,new_tests_smoothed,new_tests_smoothed_per_thousand,
# positive_rate,tests_per_case,tests_units,total_vaccinations,people_vaccinated,people_fully_vaccinated,total_boosters,new_vaccinations,new_vaccinations_smoothed,total_vaccinations_per_hundred,people_vaccinated_per_hundred,
# people_fully_vaccinated_per_hundred,total_boosters_per_hundred,new_vaccinations_smoothed_per_million,new_people_vaccinated_smoothed,new_people_vaccinated_smoothed_per_hundred,stringency_index,population,population_density,
# median_age,aged_65_older,aged_70_older,gdp_per_capita,extreme_poverty,cardiovasc_death_rate,diabetes_prevalence,female_smokers,male_smokers,handwashing_facilities,hospital_beds_per_thousand,life_expectancy,
# human_development_index,excess_mortality_cumulative_absolute,excess_mortality_cumulative,excess_mortality,excess_mortality_cumulative_per_million

In [73]:
# Depreciated
# OWID vaccine data source
# vaccine_data = "https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/vaccinations/vaccinations.csv"
# OWIDdf = pd.read_csv(vaccine_data)

# Emotion over time

In [ ]:
import datetime
WHOdf_cols = ["iso_code","country","created_at", "emotion_1"]
wd = WHOdf[WHOdf_cols]
print(f"wd.shape, wd.columns {wd.shape, wd.columns}")

emotion_list = wd.emotion_1.tolist()

wd["confidence"] = [float(i.strip('][').split(', ')[1][0:]) for i in emotion_list]
wd["emotion"] = [i.strip('][').split(', ')[0] for i in emotion_list]
wd["year"] = pd.to_datetime(wd["created_at"]).dt.year
wd["month"] = pd.to_datetime(wd["created_at"]).dt.month
# wd["date_month"] = pd.to_datetime(wd["created_at"]).dt.month
print(f"before drop {wd.shape}")

wd = wd[wd["confidence"] != 0]
wd = wd.drop(columns = ["emotion_1", "confidence", "created_at"])
print(f"after  drop {wd.shape}")

u = wd["emotion"].unique()
print(f"unique emotions: {u}")

wd.head()

wd.shape, wd.columns ((795329, 4), Index(['iso_code', 'country', 'created_at', 'emotion_1'], dtype='object'))
before drop (795329, 8)
unique emotions: ["'fear'" "'negative'" "'positive'" "'trust'" "'sadness'" "'anticipation'"
 "'anger'" "'disgust'" "'surprise'" "'joy'"]
after  drop (346665, 5)
unique emotions: ["'fear'" "'negative'" "'positive'" "'trust'" "'sadness'" "'anticipation'"
 "'anger'" "'disgust'" "'surprise'" "'joy'"]


iso_code        country     emotion  year  month
2       US  United States      'fear'  2020      1
4       PH    Philippines  'negative'  2020      1
5       SE         Sweden      'fear'  2020      1
6      NaN            NaN  'positive'  2020      1
7       CA         Canada  'positive'  2020      1

In [ ]:
wd_group = wd.groupby(["country","year", "month"])["emotion"].agg('max')#pd.Series.mode)
wd_group = wd_group.reset_index(level=0).reset_index(level=0).reset_index(level=0)

u = wd_group["emotion"].unique()
print(f"unique emotions: {u}")

wd_group.head(10)

unique emotions: ["'fear'" "'trust'" "'positive'" "'surprise'" "'anger'" "'negative'"
 "'anticipation'" "'sadness'"]


month  year      country     emotion
0      2  2020  Afghanistan      'fear'
1      3  2020  Afghanistan     'trust'
2      4  2020  Afghanistan     'trust'
3      5  2020  Afghanistan  'positive'
4      6  2020  Afghanistan     'trust'
5      7  2020  Afghanistan     'trust'
6      9  2020  Afghanistan     'trust'
7     12  2020  Afghanistan  'positive'
8      2  2021  Afghanistan     'trust'
9      3  2021  Afghanistan     'trust'

In [ ]:
# wd_group["emotion"] = wd_group["emotion"][:-1]
# wd_group.columns

In [ ]:
import numpy as np
wd_out = wd_group
# wd_out["date"] = wd_out[["year","month"]].agg('-'.join, axis=1)
wd_out["date"] = wd_out["year"] + np.round((1/12)*wd_out["month"], 2)

wd_out["emotion"].unique()

array(["'fear'", "'trust'", "'positive'", "'surprise'", "'anger'",
       "'negative'", "'anticipation'", "'sadness'"], dtype=object)

In [ ]:
col = "emotion"
wd_out = wd_out.sort_values("date")


fig = px.choropleth(wd_out,
                    locations=  'country', #"iso_code",
                    locationmode = "country names",   #"ISO-3",
                    animation_frame = "date",
                    color=col, 
                    # range_color=(min_total, max_total),
                    # color_continuous_scale=["red","yellow","green"]
)
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01
))
fig.show()

# Vaccine over time

In [ ]:
# Columns to look at:
# total_vaccinations,people_vaccinated,people_fully_vaccinated,total_boosters,new_vaccinations,new_vaccinations_smoothed,total_vaccinations_per_hundred,people_vaccinated_per_hundred,\
# people_fully_vaccinated_per_hundred,total_boosters_per_hundred,new_vaccinations_smoothed_per_million,new_people_vaccinated_smoothed,"


col = "people_vaccinated_per_hundred" # Column definitely produces a working output

In [ ]:
df = big_WHO_df[big_WHO_df["iso_code"] != "GIB"] # drop GIB as outlier
# df[["iso_code","people_fully_vaccinated_per_hundred"]].dropna().sort_values(by = "people_fully_vaccinated_per_hundred")
df2 = df[["iso_code","date", col]] # Take columns I want
df2 = df2.groupby(["date","iso_code"]).agg("max") # Take the maximum of a given date for duplicated dates
df2 = df2.reset_index(level=0).reset_index(level=0) # Get column back as a column after aggregation
df2 = df2.sort_values(["iso_code","date"]) # sort so that we can forward fill
df2 = df2.loc[df2["date"] > "2020-2-24"]  # remove old data so that the x axis scales nicely

# Forward fill using a for loop
# In an ideal scenario, a built in method would be used. If you have one feel free to simplify this
df2["iso_code_lag"] = df2["iso_code"].shift(1)
df2 = df2.reset_index() 
x = 0
for index, row in df2.iterrows():
  if (row["iso_code"] != row["iso_code_lag"]):
    x = 0
  if (pd.isna(row[col])):
    df2.at[index,col]=x
  else:
    x = row[col]
df2


In [ ]:
#Take specific column to check values
df2.loc[df2["iso_code"] =="ARG"].values.tolist()

In [ ]:
def create_choropleth(df2, col):
  max_total = df2[col].max()
  min_total = df2[col].min()

  # Chloropleth
  fig = px.choropleth(df2, # dataset to use
                    locations="iso_code", # column which includes 3 letter country code
                    locationmode = "ISO-3",
                    animation_frame = "date",
                    color=col, # column which dictates the colour of the map
                   # hover_name="location", # column to add to hover information
                    range_color=(min_total, max_total), #,# range of the colour scale
                    color_continuous_scale=["red","yellow","green"]
  )
  fig.show()

In [ ]:
create_choropleth(df2, col)

## Possible New Vaccinations

In [65]:
import numpy as np
# New Vaccine updtake
col = "new_vaccinations"

df = big_WHO_df[big_WHO_df["iso_code"] != "GIB"] # drop GIB as outlier

df2 = df[["iso_code","date", col]] # Take columns I want
df2 = df2.loc[df2["date"] > "2020-2-24"]  # remove old data so that the x axis scales nicely
df2["log_col"] = np.log(df2[col])

df2[col].max()



max_total = df2["log_col"].max()
min_total = df2["log_col"].min()

# Chloropleth
fig = px.choropleth(df2, # dataset to use
                    locations="iso_code", # column which includes 3 letter country code
                    locationmode = "ISO-3",
                    animation_frame = "date",
                    color="log_col", # column which dictates the colour of the map
                   # hover_name="location", # column to add to hover information
                    range_color=(min_total, max_total), #,# range of the colour scale
                    color_continuous_scale=["red","yellow","green"]
)
fig.show()



# df2 = df2.groupby(["date","iso_code"]).agg("max") # Take the maximum of a given date for duplicated dates
# df2 = df2.reset_index(level=0).reset_index(level=0) # Get column back as a column after aggregation
# df2 = df2.sort_values(["iso_code","date"]) # sort so that we can forward fill
# df2 = df2.loc[df2["date"] > "2020-2-24"]  # remove old data so that the x axis scales nicely

# # Forward fill using a for loop
# # In an ideal scenario, a built in method would be used. If you have one feel free to simplify this
# df2["iso_code_lag"] = df2["iso_code"].shift(1)
# df2 = df2.reset_index() 
# x = 0
# for index, row in df2.iterrows():
#   if (row["iso_code"] != row["iso_code_lag"]):
#     x = 0
#   if (pd.isna(row[col])):
#     df2.at[index,col]=x
#   else:
#     x = row[col]
# df2

/usr/local/lib/python3.7/dist-packages/pandas/core/arraylike.py:364: RuntimeWarning:

divide by zero encountered in log



# USA Sentiment/Vaccine rate

## Check columns

In [6]:
print(big_WHO_df.columns)
print()
print(WHOdf.columns)

Index(['iso_code', 'continent', 'location', 'date', 'total_cases', 'new_cases',
       'new_cases_smoothed', 'total_deaths', 'new_deaths',
       'new_deaths_smoothed', 'total_cases_per_million',
       'new_cases_per_million', 'new_cases_smoothed_per_million',
       'total_deaths_per_million', 'new_deaths_per_million',
       'new_deaths_smoothed_per_million', 'reproduction_rate', 'icu_patients',
       'icu_patients_per_million', 'hosp_patients',
       'hosp_patients_per_million', 'weekly_icu_admissions',
       'weekly_icu_admissions_per_million', 'weekly_hosp_admissions',
       'weekly_hosp_admissions_per_million', 'total_tests', 'new_tests',
       'total_tests_per_thousand', 'new_tests_per_thousand',
       'new_tests_smoothed', 'new_tests_smoothed_per_thousand',
       'positive_rate', 'tests_per_case', 'tests_units', 'total_vaccinations',
       'people_vaccinated', 'people_fully_vaccinated', 'total_boosters',
       'new_vaccinations', 'new_vaccinations_smoothed',
       't

## Select columns

In [7]:
# Taking columns:
col1 = ["location", "date", "new_cases"]

col2 = ["city","author_location", "iso_code", "country", "lat", "lng" ,"created_at","pos", "neg", "neu", "compound"]
# Locations group by:
# city - none
# author_location - probably less than iso
# iso_code - about 20 states
# counrty - none
# lat lng - 

## Exploration, can we get state information

In [102]:
print(sen.head(10))
explore = sen[sen["country"] == "United States"]
len(explore["city"].unique())

      location        date  new_cases
0  Afghanistan  2020-02-24        5.0
1  Afghanistan  2020-02-25        0.0
2  Afghanistan  2020-02-26        0.0
3  Afghanistan  2020-02-27        0.0
4  Afghanistan  2020-02-28        0.0
5  Afghanistan  2020-02-29        0.0
6  Afghanistan  2020-03-01        0.0
7  Afghanistan  2020-03-02        0.0
8  Afghanistan  2020-03-03        0.0
9  Afghanistan  2020-03-04        0.0
   index       city           author_location iso_code        country  \
0      0        NaN   National Capital Region      NaN            NaN   
1      1        NaN            Dans le hazi♥️      NaN            NaN   
2      2   Bellevue              Bellevue, WA       US  United States   
3      3    Caracas        Caracas, Venezuela       VE      Venezuela   
4      4     Manila       Manila, Philippines       PH    Philippines   
5      5  Stockholm         Stockholm, Sweden       SE         Sweden   
6      6        NaN               bhubaneswar      NaN            NaN  

3306

## Data Manipulation (USE 2)

*   Take US tweets only
*   Fill missing cities from Author_Location
*   Group by (location, date), sum sentiment
*   Sort by date







In [31]:
sen = WHOdf[col2]

col = "compound" # To be plotted
loc = "city" # Location

# Raw shape
print(f"raw shape = {sen.shape}")

# USA sentiment only
sen = sen[sen["country"] == "United States"]
print(f"United states only = {sen.shape}")

# fill in empty ISO from author_location
sen = sen.reset_index() 
for index, row in sen.iterrows():
  if (pd.isna(row["city"])):
    row["city"] = row["author_location"]
 

# Date column
sen["date"] = pd.to_datetime(sen["created_at"]).dt.date
print(f"before drop {sen.shape}")



# Group by location and date, sum sentiment
sen_group = sen.groupby(["city","date"])[["pos", "neg", "neu", "compound"]].agg('sum')
sen_group = sen_group.reset_index(level=0).reset_index(level=0)
sen_group["str_date"] = sen_group['date'].astype(str)

# State code column
sen_group["state_code"] = sen_group.apply(lambda row : us_state_to_abbrev[city_to_state_dict[row["city"]]] if (row["city"] in city_to_state_dict.keys()) else row["city"] , axis=1) # get US state code for each city

# Sort
sen_group = sen_group.sort_values("date")
sen_group = sen_group.reset_index() 

# Forwards fill compound per country
sen_group["compound_lag"] = sen_group["compound"].shift(1)
x = 0
for index, row in sen_group.iterrows():
  if (row["compound"] != row["compound_lag"]):
    x = 0
  if (pd.isna(row[col])):
    sen_group.at[index,col]=x
  else:
    x = row[col]

print(f"after group {sen_group.shape}")
sen_group

raw shape = (795329, 11)
United states only = (76381, 11)
before drop (76381, 13)
after group (52183, 10)


index        date            city    pos    neg    neu  compound  \
0       4229  2020-01-22        Bellevue  0.178  0.228  0.594   -0.1926   
1      25559  2020-01-26     Los Angeles  0.610  0.000  0.390    0.9100   
2      48057  2020-01-27          Toledo  0.000  0.338  0.662   -0.5574   
3      33092  2020-01-27   North Potomac  0.000  0.000  1.000    0.0000   
4      41840  2020-01-27  San Bernardino  0.195  0.134  0.671    0.2498   
...      ...         ...             ...    ...    ...    ...       ...   
52178  26301  2022-03-26     Los Angeles  0.000  0.000  1.000    0.0000   
52179  45693  2022-03-26         Spokane  0.000  0.000  1.000    0.0000   
52180   5959  2022-03-26          Boston  0.000  0.000  2.000    0.0000   
52181  29308  2022-03-26       Milwaukee  0.000  0.000  1.000    0.0000   
52182   5960  2022-03-27          Boston  0.000  0.000  1.000    0.0000   

         str_date state_code  compound_lag  
0      2020-01-22         NE           NaN  
1      2020-01-26         CA       -0.1926  
2      2020-01-27         OH        0.9100  
3      2020-01-27         MD       -0.5574  
4      2020-01-27         CA        0.0000  
...           ...        ...           ...  
52178  2022-03-26         CA        0.0772  
52179  2022-03-26         WA        0.0000  
52180  2022-03-26         MA        0.0000  
52181  2022-03-26         WI        0.0000  
52182  2022-03-27         MA        0.0000  

[52183 rows x 10 columns]

## Sentiment Data Manipulation 2: monthly group

*   Take US tweets only
*   Fill missing cities from Author_Location
*   Group by (location, date), sum sentiment
*   Sort by date

In [61]:
sen = WHOdf[col2]

col = "compound" # To be plotted
loc = "city" # Location

# Raw shape
print(f"raw shape = {sen.shape}")

# USA sentiment only
sen = sen[sen["country"] == "United States"]
print(f"United states only = {sen.shape}")

# fill in empty ISO from author_location
sen = sen.reset_index() 
for index, row in sen.iterrows():
  if (pd.isna(row["city"])):
    row["city"] = row["author_location"]

# Date column
sen["date_year"] = pd.to_datetime(sen["created_at"]).dt.year
sen["date_month"] = pd.to_datetime(sen["created_at"]).dt.month
print(f"before drop {sen.shape}")

# State code column
sen["state_code"] = sen.apply(lambda row : us_state_to_abbrev[city_to_state_dict[row["city"]]] if (row["city"] in city_to_state_dict.keys()) else row["city"] , axis=1) # get US state code for each city

# Date from year and months to group by each month
sen["date"] = sen["date_year"] + np.round((1/12)*sen["date_month"], 2)

# Group by location and date, sum sentiment
sen_group = sen.groupby(["state_code","date"])[["pos", "neg", "neu", "compound"]].agg('mean')
sen_group = sen_group.reset_index(level=0)
# sen_group["str_date"] = sen_group['date'].astype(str)

# Sort
sen_group = sen_group.sort_values("date")
sen_group = sen_group.reset_index() 

# Forwards fill compound per country
# sen_group["compound_lag"] = sen_group["compound"].shift(1)
# x = 0
# for index, row in sen_group.iterrows():
#   if (row["compound"] != row["compound_lag"]):
#     x = 0
#   if (pd.isna(row[col])):
#     sen_group.at[index,col]=x
#   else:
#     x = row[col]

print(f"after group {sen_group.shape}")
sen_group

raw shape = (795329, 11)
United states only = (76381, 11)
before drop (76381, 14)
after group (6390, 6)


date state_code       pos       neg       neu  compound
0     2020.08         AK  0.000000  0.097000  0.903000 -0.421500
1     2020.08         PA  0.061000  0.131400  0.807600 -0.133820
2     2020.08         MO  0.216000  0.000000  0.784000  0.526700
3     2020.08   Homeland  0.000000  0.249000  0.751000 -0.510600
4     2020.08         MN  0.052333  0.138000  0.809333 -0.225100
...       ...        ...       ...       ...       ...       ...
6385  2022.25         MS  0.031333  0.000000  0.968667  0.133967
6386  2022.25         WI  0.066556  0.077778  0.855667 -0.015033
6387  2022.25   Broadway  0.000000  0.147000  0.853000 -0.341200
6388  2022.25         OK  0.000000  0.000000  1.000000  0.000000
6389  2022.25         WA  0.040526  0.029684  0.929842  0.035063

[6390 rows x 6 columns]

# Choropleth

In [64]:
max_total = sen_group[col].max()
min_total = sen_group[col].min()

fig = px.choropleth(sen_group, # dataset to use
                    locations="state_code", # column which includes 3 letter country code
                    locationmode =  "USA-states", #"country names", #
                    animation_frame = "date",
                    scope="usa",
                    color= col, # column which dictates the colour of the map
                   # hover_name="location", # column to add to hover information
                    range_color= (-0.5,0.5), #(min_total, max_total), #,# range of the colour scale
                    color_continuous_midpoint = 0,
                    color_continuous_scale= [[1, "red"], [0.1, "yellow"], [1, "green"]] #["red","yellow","green"]                          
)
fig.show()

# lat = "lat",
# lon = "lng",

## Sentiment Data Manipulation 2: monthly group

*   Take US tweets only
*   Fill missing cities from Author_Location
*   Group by (location, date), sum sentiment
*   Sort by date

In [80]:
vax = big_WHO_df[col1]

col = "compound" # To be plotted
loc = "city" # Location

# Raw shape
print(f"raw shape = {vax.shape}")

# USA sentiment only
vax = vax[vax["location"] == "United States"]
print(f"United states only = {vax.shape}")

# Date column
vax["date_year"] = pd.to_datetime(vax["date"]).dt.year
vax["date_month"] = pd.to_datetime(vax["date"]).dt.month

# Date from year and months to group by each month
vax["date"] = vax["date_year"] + np.round((1/12)*vax["date_month"], 2)
print(f"before drop {vax.shape}")


# Group by location and date, sum sentiment
vax_group = vax.groupby(["date"])[["new_cases"]].agg('sum')
vax_group = vax_group.reset_index(level=0)
# sen_group["str_date"] = sen_group['date'].astype(str)
print(vax_group.head(10))

# # fill in empty ISO from author_location
# sen = sen.reset_index() 
# for index, row in sen.iterrows():
#   if (pd.isna(row["city"])):
#     row["city"] = row["author_location"]


# # State code column
# sen["state_code"] = sen.apply(lambda row : us_state_to_abbrev[city_to_state_dict[row["city"]]] if (row["city"] in city_to_state_dict.keys()) else row["city"] , axis=1) # get US state code for each city



# # Sort
# sen_group = sen_group.sort_values("date")
# sen_group = sen_group.reset_index() 

# # Forwards fill compound per country
# # sen_group["compound_lag"] = sen_group["compound"].shift(1)
# # x = 0
# # for index, row in sen_group.iterrows():
# #   if (row["compound"] != row["compound_lag"]):
# #     x = 0
# #   if (pd.isna(row[col])):
# #     sen_group.at[index,col]=x
# #   else:
# #     x = row[col]

# print(f"after group {sen_group.shape}")
# sen_group


raw shape = (169939, 3)
United states only = (789, 3)
before drop (789, 5)
      date  new_cases
0  2020.08        7.0
1  2020.17       17.0
2  2020.25   192054.0
3  2020.33   884399.0
4  2020.42   711709.0
5  2020.50   856859.0
6  2020.58  1898535.0
7  2020.67  1499164.0
8  2020.75  1197031.0
9  2020.83  1916423.0


# Method from our Github

In [ ]:
!pip install pycountry
from turtle import position
import pandas as pd
import json
import matplotlib.pyplot as plt
import pycountry
import datetime
from scipy.stats import pearsonr
import numpy as np

In [97]:
def normaliseCC(row):
    code = row['iso_code']
    iso3 = pycountry.countries.get(alpha_2=code)
    if iso3:
        return iso3.alpha_3
    else:
        return code

def cleanTweetDF(df):
    df = df[df["iso_code"].notna()]
    df = df[df["created_at"].notna()]
    df['iso_code'] = df.apply(lambda row : normaliseCC(row), axis=1) #normalise country codes to standard iso where exists
    return df.copy()

def groupDFByMonth(iso_col_name, code, df):
    isCountry = df[iso_col_name]==code
    df = df[isCountry]
    dates = pd.to_datetime(df['created_at'])
    df['created_at'] = dates
    df = df.set_index('created_at')
    return df.groupby(pd.Grouper(freq='M')).mean()


sen2 = cleanTweetDF(WHOdf[col2])
# print(sen2)

# Date column
sen2["date"] = pd.to_datetime(sen["created_at"]).dt.date
print(f"before drop {sen.shape}")

# Group by location and date, sum sentiment
sen2 = sen2.groupby([loc,"date"])[["pos", "neg", "neu", "compound"]].agg('sum')
sen2 = sen2.reset_index(level=0).reset_index(level=0)
sen2["str_date"] = sen2['date'].astype(str)

# Sort
sen2 = sen2.sort_values("date")

sen2

before drop (795329, 13)


date iso_code    pos    neg    neu  compound    str_date
31384  2020-01-22      VEN  0.000  0.000  1.000    0.0000  2020-01-22
30568  2020-01-22      USA  0.178  0.228  0.594   -0.1926  2020-01-22
24477  2020-01-23      PHL  0.055  0.047  0.898    0.0516  2020-01-23
28050  2020-01-23      SWE  0.000  0.187  0.813   -0.5994  2020-01-23
4776   2020-01-24      CAN  0.000  0.071  0.929   -0.3818  2020-01-24
...           ...      ...    ...    ...    ...       ...         ...
20292  2022-03-26      MEX  0.000  0.000  1.000    0.0000  2022-03-26
32134  2022-03-26      VEN  0.000  0.000  1.000    0.0000  2022-03-26
26469  2022-03-27      ROU  0.171  0.343  0.485   -0.7213  2022-03-27
32135  2022-03-27      VEN  0.000  0.000  1.000    0.0000  2022-03-27
31359  2022-03-27      USA  0.000  0.000  1.000    0.0000  2022-03-27

[33217 rows x 7 columns]

In [99]:
max_total = sen[col].max()
min_total = sen[col].min()

fig = px.choropleth(sen2, # dataset to use
                    locations="iso_code", # column which includes 3 letter country code
                    locationmode =  "USA-states", #"country names", #
                    animation_frame = "str_date",
                    scope="usa",
                    color= col, # column which dictates the colour of the map
                   # hover_name="location", # column to add to hover information
                    range_color=(min_total, max_total), #,# range of the colour scale
                    color_continuous_scale=["red","yellow","green"]
)
fig.show()

# CITY -> STATE CODE dictionary

https://galeascience.wordpress.com/2016/03/23/us-city-to-state-python-dictionary/

In [1]:
# City to USA state code
# the Geonamescache library contains information
# about continents, cities and US states
!pip install geonamescache
import geonamescache
 
# finding the state based on geotags
# (i.e. longitude and latitude)
from geopy.geocoders import Nominatim

In [ ]:
# get a dictionary of cities: 'c'
gc = geonamescache.GeonamesCache()
c = gc.get_cities()
 
# extract the US city names and coordinates
US_cities = [c[key]['name'] for key in list(c.keys())
             if c[key]['countrycode'] == 'US']
US_longs = [c[key]['longitude'] for key in list(c.keys())
            if c[key]['countrycode'] == 'US']
US_latts = [c[key]['latitude'] for key in list(c.keys())
            if c[key]['countrycode'] == 'US']

def get_states(longs, latts):
    ''' Input two 1D lists of floats/ints '''
# a list of states
    states = []
 
    # use a coordinate tool from the geopy library
    geolocator = Nominatim()
    for lon, lat in zip(longs, latts):
        try:
            # get the state name
            location = geolocator.reverse(str(lat)+', '+str(lon))
            state = location.raw['address']['state']
        except:
            # return empty string
            state = ''
        states.append(state)
    return states

# find the states of each city
# WARNING: this takes a while
US_states = get_states(US_longs, US_latts)

city_to_state = {}
for city, state in zip(US_cities, US_states):
    if state:
        city_to_state[city] = state

/usr/local/lib/python3.7/dist-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


In [ ]:
# import pickle

# Use pickle to save dict
# with open('saved_city_to_state.pkl', 'wb') as f:
#     pickle.dump(city_to_state, f)

# Use pickle to open dict     
# with open('saved_city_to_state.pkl', 'rb') as f:
#     city_to_state = pickle.load(f)

In [25]:
us_state_to_abbrev = {
    "Alabama": "AL",
    "Alaska": "AK",
    "Arizona": "AZ",
    "Arkansas": "AR",
    "California": "CA",
    "Colorado": "CO",
    "Connecticut": "CT",
    "Delaware": "DE",
    "Florida": "FL",
    "Georgia": "GA",
    "Hawaii": "HI",
    "Idaho": "ID",
    "Illinois": "IL",
    "Indiana": "IN",
    "Iowa": "IA",
    "Kansas": "KS",
    "Kentucky": "KY",
    "Louisiana": "LA",
    "Maine": "ME",
    "Maryland": "MD",
    "Massachusetts": "MA",
    "Michigan": "MI",
    "Minnesota": "MN",
    "Mississippi": "MS",
    "Missouri": "MO",
    "Montana": "MT",
    "Nebraska": "NE",
    "Nevada": "NV",
    "New Hampshire": "NH",
    "New Jersey": "NJ",
    "New Mexico": "NM",
    "New York": "NY",
    "North Carolina": "NC",
    "North Dakota": "ND",
    "Ohio": "OH",
    "Oklahoma": "OK",
    "Oregon": "OR",
    "Pennsylvania": "PA",
    "Rhode Island": "RI",
    "South Carolina": "SC",
    "South Dakota": "SD",
    "Tennessee": "TN",
    "Texas": "TX",
    "Utah": "UT",
    "Vermont": "VT",
    "Virginia": "VA",
    "Washington": "WA",
    "West Virginia": "WV",
    "Wisconsin": "WI",
    "Wyoming": "WY",
    "District of Columbia": "DC",
    "American Samoa": "AS",
    "Guam": "GU",
    "Northern Mariana Islands": "MP",
    "Puerto Rico": "PR",
    "United States Minor Outlying Islands": "UM",
    "U.S. Virgin Islands": "VI",
}

In [4]:
city_to_state_dict = {"East Rancho Dominguez": "California",
                      "Clinton": "Mississippi",
                      "Nanuet": "New York",
                      "Sand Springs": "Oklahoma",
                      "Middle River": "Maryland",
                      "Carbondale": "Illinois",
                      "Boise": "Idaho",
                      "Las Vegas": "Nevada",
                      "Denver": "Colorado",
                      "Hagerstown": "Maryland",
                      "Venice": "Florida",
                      "Moreno Valley": "California",
                      "Mamaroneck": "New York",
                      "Bartow": "Florida",
                      "Bensonhurst": "New York",
                      "Edgewater": "Florida",
                      "Dallas": "Texas",
                      "Benton": "Arkansas",
                      "Lake Havasu City": "Arizona",
                      "New South Memphis": "Tennessee",
                      "North Glendale": "California",
                      "Santee": "California",
                      "Shawnee": "Oklahoma",
                      "North Augusta": "South Carolina",
                      "Brownwood": "Texas",
                      "Methuen": "Massachusetts",
                      "Allapattah": "Florida",
                      "White Oak": "Maryland",
                      "University Place": "Washington",
                      "Muncie": "Indiana",
                      "Naperville": "Illinois",
                      "Hollywood": "Florida",
                      "Richmond West": "Florida",
                      "Bellmore": "New York",
                      "Pine Bluff": "Arkansas",
                      "Natick": "Massachusetts",
                      "Silver Lake": "California",
                      "Ridgecrest": "California",
                      "Parkland": "Washington",
                      "Aberdeen": "Washington",
                      "Cohoes": "New York",
                      "Harlingen": "Texas",
                      "Ennis": "Texas",
                      "North La Crosse": "Wisconsin",
                      "Commerce City": "Colorado",
                      "Racine": "Wisconsin",
                      "Carmel": "Indiana",
                      "Fairview Park": "Ohio",
                      "Queen Creek": "Arizona",
                      "Southglenn": "Colorado",
                      "Wentzville": "Missouri",
                      "Pinecrest": "Florida",
                      "Kingston": "New York",
                      "Syracuse": "New York",
                      "El Cajon": "California",
                      "Champaign": "Illinois",
                      "Stevens Point": "Wisconsin",
                      "San Luis": "Arizona",
                      "Livingston": "New Jersey",
                      "Santa Maria": "California",
                      "Fort Leonard Wood": "Missouri",
                      "West Elkridge": "Maryland",
                      "New Iberia": "Louisiana",
                      "Elk Grove": "California",
                      "Smithtown": "New York",
                      "Greensboro": "North Carolina",
                      "Garden Grove": "California",
                      "Emporia": "Kansas",
                      "Sun Valley": "Nevada",
                      "Wheeling": "West Virginia",
                      "Troy": "Ohio",
                      "Irving": "Connecticut",
                      "Cornelius": "North Carolina",
                      "East Cleveland": "Ohio",
                      "Upland": "California",
                      "Porterville": "California",
                      "Rock Island": "Illinois",
                      "Prattville": "Alabama",
                      "Aloha": "Oregon",
                      "Durham": "North Carolina",
                      "Lynnwood": "Washington",
                      "Dunwoody": "Georgia",
                      "East New York": "New York",
                      "Santa Clara": "California",
                      "Homestead": "Florida",
                      "Borough of Queens": "New York",
                      "Woodland": "California",
                      "Pennsauken": "New Jersey",
                      "Marrero": "Louisiana",
                      "Meadow Woods": "Florida",
                      "Godfrey": "Illinois",
                      "Apache Junction": "Arizona",
                      "Oak Grove": "Oregon",
                      "Surprise": "Arizona",
                      "Lake Oswego": "Oregon",
                      "Goleta": "California",
                      "Tullahoma": "Tennessee",
                      "Kinston": "North Carolina",
                      "Vernon Hills": "Illinois",
                      "Agoura": "California",
                      "Grants Pass": "Oregon",
                      "Topeka": "Kansas",
                      "West New York": "New Jersey",
                      "Grand Forks": "North Dakota",
                      "Cedar Falls": "Iowa",
                      "Minot": "North Dakota",
                      "Carrollton": "Georgia",
                      "West Little River": "Florida",
                      "Huntington Beach": "California",
                      "Newark": "Ohio",
                      "Bellflower": "California",
                      "Wilmington Island": "Georgia",
                      "Country Club": "Florida",
                      "Hazleton": "Pennsylvania",
                      "Burton": "Michigan",
                      "Eureka": "California",
                      "Vincennes": "Indiana",
                      "Monroe": "Washington",
                      "Kernersville": "North Carolina",
                      "Clayton": "Missouri",
                      "Chester": "Pennsylvania",
                      "Caldwell": "Idaho",
                      "Cloverleaf": "Texas",
                      "Brandon": "Mississippi",
                      "Mishawaka": "Indiana",
                      "Winter Springs": "Florida",
                      "Clarksville": "Indiana",
                      "West Warwick": "Rhode Island",
                      "Dunedin": "Florida",
                      "Eldersburg": "Maryland",
                      "Orland Park": "Illinois",
                      "Palm Valley": "Florida",
                      "Holly Springs": "North Carolina",
                      "Maplewood": "New Jersey",
                      "Carrboro": "North Carolina",
                      "Escondido": "California",
                      "Xenia": "Ohio",
                      "Santa Clarita": "California",
                      "Vicksburg": "Mississippi",
                      "Farmers Branch": "Texas",
                      "Mill Creek": "Washington",
                      "Naples": "Florida",
                      "Cedar Hill": "Texas",
                      "Indian Trail": "North Carolina",
                      "Shrewsbury": "Massachusetts",
                      "Mead Valley": "California",
                      "Crown Point": "Indiana",
                      "Blythe": "California",
                      "Centerville": "Utah",
                      "Bothell": "Washington",
                      "American Fork": "Utah",
                      "Casselberry": "Florida",
                      "Chesterfield": "Missouri",
                      "North Olmsted": "Ohio",
                      "Rocky Mount": "North Carolina",
                      "Americus": "Georgia",
                      "Madera": "California",
                      "Port Washington": "New York",
                      "Branford": "Connecticut",
                      "Chickasha": "Oklahoma",
                      "South Bradenton": "Florida",
                      "Oxnard Shores": "California",
                      "Huntley": "Illinois",
                      "Scottsdale": "Arizona",
                      "Palm Coast": "Florida",
                      "Homewood": "Alabama",
                      "Berwyn": "Illinois",
                      "Huber Heights": "Ohio",
                      "Bay Village": "Ohio",
                      "Eagle Pass": "Texas",
                      "Plainview": "Texas",
                      "Gloversville": "New York",
                      "South Portland": "Maine",
                      "Wantagh": "New York",
                      "Staten Island": "New York",
                      "Angleton": "Texas",
                      "Woodburn": "Oregon",
                      "Rockville": "Maryland",
                      "Monterey Park": "California",
                      "Montclair": "New Jersey",
                      "Brockton": "Massachusetts",
                      "Cincinnati": "Ohio",
                      "Somerset": "New Jersey",
                      "Bentonville": "Arkansas",
                      "Elgin": "Illinois",
                      "South Elgin": "Illinois",
                      "Rockland": "Massachusetts",
                      "Bensenville": "Illinois",
                      "San Francisco": "California",
                      "Mukilteo": "Washington",
                      "Merritt Island": "Florida",
                      "Avocado Heights": "California",
                      "Corpus Christi": "Texas",
                      "Altamonte Springs": "Florida",
                      "Ellicott City": "Maryland",
                      "North Royalton": "Ohio",
                      "Toms River": "New Jersey",
                      "Forrest City": "Arkansas",
                      "Kihei": "Hawaii",
                      "Colonia": "New Jersey",
                      "Prairieville": "Louisiana",
                      "South Valley": "New Mexico",
                      "Waipahu": "Hawaii",
                      "Florin": "California",
                      "Rio Linda": "California",
                      "Highlands Ranch": "Colorado",
                      "Crest Hill": "Illinois",
                      "Yarmouth": "Massachusetts",
                      "Augusta": "Georgia",
                      "Bremerton": "Washington",
                      "Lavergne": "Tennessee",
                      "Millcreek": "Utah",
                      "Evanston": "Illinois",
                      "De Pere": "Wisconsin",
                      "Paducah": "Kentucky",
                      "Fremont": "California",
                      "Four Corners": "Oregon",
                      "Lenexa": "Kansas",
                      "Covington": "Washington",
                      "Mustang": "Oklahoma",
                      "Calexico": "California",
                      "Barstow": "California",
                      "Ferndale": "Michigan",
                      "Oklahoma City": "Oklahoma",
                      "Magna": "Utah",
                      "Tahlequah": "Oklahoma",
                      "El Dorado": "Arkansas",
                      "McAlester": "Oklahoma",
                      "Levittown": "New York",
                      "South Whittier": "California",
                      "Huntington": "New York",
                      "McMinnville": "Oregon",
                      "Irondequoit": "New York",
                      "DeBary": "Florida",
                      "Westfield": "Massachusetts",
                      "Castaic": "California",
                      "Villa Park": "Illinois",
                      "Erlanger": "Kentucky",
                      "Bryan": "Texas",
                      "San Jose": "California",
                      "Matthews": "North Carolina",
                      "Maryville": "Tennessee",
                      "Oroville": "California",
                      "Weirton": "West Virginia",
                      "Poinciana": "Florida",
                      "South Peabody": "Massachusetts",
                      "Rohnert Park": "California",
                      "North Kingstown": "Rhode Island",
                      "Spanish Lake": "Missouri",
                      "Hobart": "Indiana",
                      "Rahway": "New Jersey",
                      "Navarre": "Florida",
                      "Harker Heights": "Texas",
                      "Kenosha": "Wisconsin",
                      "West Babylon": "New York",
                      "Marshalltown": "Iowa",
                      "Madison": "New Jersey",
                      "Warrensburg": "Missouri",
                      "Boulder City": "Nevada",
                      "Colleyville": "Texas",
                      "Winchester": "Kentucky",
                      "Lafayette": "Louisiana",
                      "Parsippany": "New Jersey",
                      "Orchards": "Washington",
                      "Center Point": "Alabama",
                      "Crofton": "Maryland",
                      "Royal Palm Beach": "Florida",
                      "Herriman": "Utah",
                      "East Patchogue": "New York",
                      "West Torrington": "Connecticut",
                      "The Crossings": "Florida",
                      "Everett": "Massachusetts",
                      "Austin": "Minnesota",
                      "Tamarac": "Florida",
                      "Arroyo Grande": "California",
                      "Fort Lauderdale": "Florida",
                      "Norfolk": "Nebraska",
                      "Valparaiso": "Indiana",
                      "New Rochelle": "New York",
                      "Vandalia": "Ohio",
                      "Casas Adobes": "Arizona",
                      "Taunton": "Massachusetts",
                      "Morgan Hill": "California",
                      "Council Bluffs": "Iowa",
                      "Cottage Lake": "Washington",
                      "Bethesda": "Maryland",
                      "Centereach": "New York",
                      "Urbana": "Illinois",
                      "Hays": "Kansas",
                      "Lomita": "California",
                      "Ilchester": "Maryland",
                      "Webster Groves": "Missouri",
                      "Southfield": "Michigan",
                      "Lawton": "Oklahoma",
                      "Carol City": "Florida",
                      "North Bethesda": "Maryland",
                      "Lake Magdalene": "Florida",
                      "Rio Rico": "Arizona",
                      "Avon Center": "Ohio",
                      "Skokie": "Illinois",
                      "Logan": "Utah",
                      "Amarillo": "Texas",
                      "Shoreline": "Washington",
                      "Coppell": "Texas",
                      "Pearl River": "New York",
                      "Titusville": "Florida",
                      "Orem": "Utah",
                      "Cary": "Illinois",
                      "Fairview Heights": "Illinois",
                      "Acworth": "Georgia",
                      "Golden": "Colorado",
                      "Gardner": "Kansas",
                      "Lombard": "Illinois",
                      "Dania Beach": "Florida",
                      "Maple Heights": "Ohio",
                      "Casa de Oro-Mount Helix": "California",
                      "Brownsville": "Florida",
                      "Chicago": "Illinois",
                      "Largo": "Florida",
                      "Papillion": "Nebraska",
                      "Menomonee Falls": "Wisconsin",
                      "Jacksonville Beach": "Florida",
                      "Hopkinsville": "Kentucky",
                      "Ocala": "Florida",
                      "Defiance": "Ohio",
                      "Texarkana": "Arkansas",
                      "Warwick": "Rhode Island",
                      "Bonita Springs": "Florida",
                      "Garner": "North Carolina",
                      "Vineyard": "California",
                      "Great Falls": "Montana",
                      "Downey": "California",
                      "West Haven": "Connecticut",
                      "Goose Creek": "South Carolina",
                      "Menasha": "Wisconsin",
                      "Fountain Valley": "California",
                      "Evansville": "Indiana",
                      "Radcliff": "Kentucky",
                      "Tampa": "Florida",
                      "Sherman Oaks": "California",
                      "Aliso Viejo": "California",
                      "Belvidere": "Illinois",
                      "Lithia Springs": "Georgia",
                      "Russellville": "Arkansas",
                      "Swansea": "Massachusetts",
                      "Ferguson": "Missouri",
                      "Tigard": "Oregon",
                      "Bradenton": "Florida",
                      "Geneva": "Illinois",
                      "Salt Lake City": "Utah",
                      "Grove City": "Ohio",
                      "Calverton": "Maryland",
                      "Eastpointe": "Michigan",
                      "Fallbrook": "California",
                      "Payson": "Arizona",
                      "Melrose": "Massachusetts",
                      "Palm Desert": "California",
                      "State College": "Pennsylvania",
                      "Marion": "Ohio",
                      "Rochester": "New York",
                      "Milledgeville": "Georgia",
                      "New Smyrna Beach": "Florida",
                      "Severn": "Maryland",
                      "Columbus": "Georgia",
                      "Junction City": "Kansas",
                      "West Valley City": "Utah",
                      "Sudbury": "Massachusetts",
                      "Hauppauge": "New York",
                      "Greeley": "Colorado",
                      "Altus": "Oklahoma",
                      "Pompano Beach": "Florida",
                      "Mountain View": "California",
                      "Manhattan": "New York",
                      "South Lake Tahoe": "California",
                      "Wausau": "Wisconsin",
                      "Ridgewood": "New Jersey",
                      "Hacienda Heights": "California",
                      "Miami Gardens": "Florida",
                      "Belton": "Missouri",
                      "Wooster": "Ohio",
                      "Sunnyvale": "California",
                      "Channelview": "Texas",
                      "Waukesha": "Wisconsin",
                      "Fishers": "Indiana",
                      "Brighton": "Colorado",
                      "Calhoun": "Georgia",
                      "Fort Hood": "Texas",
                      "Owings Mills": "Maryland",
                      "Lauderdale Lakes": "Florida",
                      "Roosevelt": "New York",
                      "East Independence": "Missouri",
                      "Juneau": "Alaska",
                      "Golden Gate": "Florida",
                      "Foster City": "California",
                      "Kalispell": "Montana",
                      "South Hadley": "Massachusetts",
                      "Findlay": "Ohio",
                      "Huntington Station": "New York",
                      "Trussville": "Alabama",
                      "Baldwin Park": "California",
                      "Prairie Village": "Kansas",
                      "LaPorte": "Indiana",
                      "Newport": "Rhode Island",
                      "Lebanon": "Tennessee",
                      "South Holland": "Illinois",
                      "Albuquerque": "New Mexico",
                      "Hattiesburg": "Mississippi",
                      "Chowchilla": "California",
                      "Sun City West": "Arizona",
                      "Lincoln Park": "Michigan",
                      "Carlsbad": "New Mexico",
                      "Tallahassee": "Florida",
                      "Buenaventura Lakes": "Florida",
                      "Ceres": "California",
                      "Mercer Island": "Washington",
                      "Talladega": "Alabama",
                      "Fairland": "Maryland",
                      "San Dimas": "California",
                      "Rapid City": "South Dakota",
                      "Newburg": "Kentucky",
                      "Brent": "Florida",
                      "Yuma": "Arizona",
                      "Northridge": "California",
                      "Paragould": "Arkansas",
                      "West Gulfport": "Mississippi",
                      "Euless": "Texas",
                      "Lake Stevens": "Washington",
                      "Goodings Grove": "Illinois",
                      "Bel Air South": "Maryland",
                      "Haltom City": "Texas",
                      "Camp Springs": "Maryland",
                      "Troutdale": "Oregon",
                      "National City": "California",
                      "Edinburg": "Texas",
                      "Point Pleasant": "New Jersey",
                      "La Grange": "Illinois",
                      "Socorro Mission Number 1 Colonia": "Texas",
                      "Cape Girardeau": "Missouri",
                      "Upper Saint Clair": "Pennsylvania",
                      "Florence": "Alabama",
                      "Bridgewater": "New Jersey",
                      "Raymore": "Missouri",
                      "New Berlin": "Wisconsin",
                      "Dearborn Heights": "Michigan",
                      "Detroit": "Michigan",
                      "Flint": "Michigan",
                      "Tulare": "California",
                      "Marlboro": "New Jersey",
                      "Castro Valley": "California",
                      "Lino Lakes": "Minnesota",
                      "Calumet City": "Illinois",
                      "Peekskill": "New York",
                      "Mequon": "Wisconsin",
                      "Roseville": "California",
                      "Fort Hunt": "Virginia",
                      "Reisterstown": "Maryland",
                      "Moorhead": "Minnesota",
                      "Mooresville": "North Carolina",
                      "Natchitoches": "Louisiana",
                      "Agawam": "Massachusetts",
                      "Crestview": "Florida",
                      "Willingboro": "New Jersey",
                      "Hoffman Estates": "Illinois",
                      "Sterling Heights": "Michigan",
                      "Cliffside Park": "New Jersey",
                      "Nashua": "New Hampshire",
                      "Madison Heights": "Michigan",
                      "New York City": "New York",
                      "Palmetto Bay": "Florida",
                      "Dundalk": "Maryland",
                      "Calabasas": "California",
                      "Olney": "Maryland",
                      "Maryland Heights": "Missouri",
                      "Lewiston Orchards": "Idaho",
                      "Newnan": "Georgia",
                      "Glen Burnie": "Maryland",
                      "Sun Prairie": "Wisconsin",
                      "Cockeysville": "Maryland",
                      "North Creek": "Washington",
                      "Derby": "Kansas",
                      "Coconut Creek": "Florida",
                      "Murfreesboro": "Tennessee",
                      "Parker": "Colorado",
                      "Arbutus": "Maryland",
                      "Loveland": "Colorado",
                      "Susanville": "California",
                      "Chalmette": "Louisiana",
                      "Saint Cloud": "Florida",
                      "Edison": "New Jersey",
                      "Cedar Rapids": "Iowa",
                      "Beaumont": "Texas",
                      "Flowing Wells": "Arizona",
                      "Patterson": "California",
                      "Summit": "New Jersey",
                      "Pinewood": "Florida",
                      "Owosso": "Michigan",
                      "Antelope": "California",
                      "Greer": "South Carolina",
                      "Jackson": "Michigan",
                      "Dodge City": "Kansas",
                      "Ponte Vedra Beach": "Florida",
                      "Palatine": "Illinois",
                      "La Crosse": "Wisconsin",
                      "Columbia Heights": "Minnesota",
                      "Pinellas Park": "Florida",
                      "Chico": "California",
                      "Kuna": "Idaho",
                      "Gretna": "Louisiana",
                      "Ewing": "New Jersey",
                      "Parole": "Maryland",
                      "Hannibal": "Missouri",
                      "Hillsboro": "Oregon",
                      "Alamogordo": "New Mexico",
                      "Carol Stream": "Illinois",
                      "Willoughby": "Ohio",
                      "South Bend": "Indiana",
                      "Pacific Grove": "California",
                      "Jamaica Plain": "Massachusetts",
                      "Griffith": "Indiana",
                      "North Bellmore": "New York",
                      "South Euclid": "Ohio",
                      "Valley Stream": "New York",
                      "O'Fallon": "Illinois",
                      "Onalaska": "Wisconsin",
                      "Crawfordsville": "Indiana",
                      "Aldine": "Texas",
                      "Post Falls": "Idaho",
                      "Rexburg": "Idaho",
                      "Ponca City": "Oklahoma",
                      "Kaysville": "Utah",
                      "St. Marys": "Georgia",
                      "Shenandoah": "Louisiana",
                      "Westbury": "New York",
                      "Wasco": "California",
                      "Maitland": "Florida",
                      "Fortuna Foothills": "Arizona",
                      "Frankfort": "Kentucky",
                      "Battle Creek": "Michigan",
                      "Paterson": "New Jersey",
                      "Tualatin": "Oregon",
                      "Murrysville": "Pennsylvania",
                      "Balch Springs": "Texas",
                      "Rio Rancho": "New Mexico",
                      "Selden": "New York",
                      "Jersey City": "New Jersey",
                      "Chandler": "Arizona",
                      "Fort Walton Beach": "Florida",
                      "New Milford": "New Jersey",
                      "Newberg": "Oregon",
                      "Affton": "Missouri",
                      "Kaneohe": "Hawaii",
                      "Hinesville": "Georgia",
                      "Lexington-Fayette": "Kentucky",
                      "Nutley": "New Jersey",
                      "Pekin": "Illinois",
                      "Summerville": "South Carolina",
                      "Lake Forest": "Illinois",
                      "Glendale": "California",
                      "Flower Mound": "Texas",
                      "Fond du Lac": "Wisconsin",
                      "Ruston": "Louisiana",
                      "Valrico": "Florida",
                      "Melrose Park": "Illinois",
                      "Radnor": "Pennsylvania",
                      "Shelbyville": "Indiana",
                      "Henderson": "North Carolina",
                      "Raleigh": "North Carolina",
                      "Schaumburg": "Illinois",
                      "Perry Hall": "Maryland",
                      "West Bloomfield Township": "Michigan",
                      "Terrytown": "Louisiana",
                      "Rancho Cordova": "California",
                      "Bella Vista": "Arkansas",
                      "Olive Branch": "Mississippi",
                      "Cocoa": "Florida",
                      "Longview": "Washington",
                      "Hamtramck": "Michigan",
                      "Randallstown": "Maryland",
                      "Hesperia": "California",
                      "Five Corners": "Washington",
                      "East Brainerd": "Tennessee",
                      "Mineola": "New York",
                      "Opa-locka": "Florida",
                      "Littleton": "Colorado",
                      "South Jordan Heights": "Utah",
                      "Albemarle": "North Carolina",
                      "Gillette": "Wyoming",
                      "North Platte": "Nebraska",
                      "Montgomery": "Alabama",
                      "North Highlands": "California",
                      "Brea": "California",
                      "South Miami Heights": "Florida",
                      "Avenal": "California",
                      "Lancaster": "Ohio",
                      "Brownsburg": "Indiana",
                      "Ormond Beach": "Florida",
                      "Coos Bay": "Oregon",
                      "Pembroke Pines": "Florida",
                      "Claremore": "Oklahoma",
                      "Gastonia": "North Carolina",
                      "East Saint Louis": "Illinois",
                      "Sterling": "Illinois",
                      "Lake Worth Corridor": "Florida",
                      "Selma": "California",
                      "Seven Oaks": "South Carolina",
                      "Rancho Mirage": "California",
                      "Wake Forest": "North Carolina",
                      "Gahanna": "Ohio",
                      "Richmond": "Kentucky",
                      "Park Forest": "Illinois",
                      "Wethersfield": "Connecticut",
                      "Douglasville": "Georgia",
                      "Laurel": "Mississippi",
                      "Homer Glen": "Illinois",
                      "Fountain": "Colorado",
                      "San Marcos": "California",
                      "Copiague": "New York",
                      "Matteson": "Illinois",
                      "North Tonawanda": "New York",
                      "Stockton": "California",
                      "Statesboro": "Georgia",
                      "Fargo": "North Dakota",
                      "West Lake Stevens": "Washington",
                      "Corona": "California",
                      "Cutler Bay": "Florida",
                      "Seaside": "California",
                      "Shively": "Kentucky",
                      "Hemet": "California",
                      "Billerica": "Massachusetts",
                      "Amesbury": "Massachusetts",
                      "Spring Valley": "New York",
                      "Chino": "California",
                      "Great Bend": "Kansas",
                      "Bossier City": "Louisiana",
                      "Windsor": "Colorado",
                      "Riverside": "Ohio",
                      "Limerick": "Pennsylvania",
                      "Blaine": "Minnesota",
                      "Paramount": "California",
                      "Lynbrook": "New York",
                      "Eggertsville": "New York",
                      "Ballwin": "Missouri",
                      "Gresham": "Oregon",
                      "Saint Charles": "Missouri",
                      "Saint Matthews": "Kentucky",
                      "Nashville": "Tennessee",
                      "North Babylon": "New York",
                      "Holtsville": "New York",
                      "Southchase": "Florida",
                      "Sanger": "California",
                      "Eloy": "Arizona",
                      "Daly City": "California",
                      "Bedford": "New Hampshire",
                      "Kennewick": "Washington",
                      "Cranston": "Rhode Island",
                      "Garden City": "New York",
                      "Wellesley": "Massachusetts",
                      "Ypsilanti": "Michigan",
                      "Tinton Falls": "New Jersey",
                      "Alamo": "Texas",
                      "Bryn Mawr-Skyway": "Washington",
                      "Roswell": "Georgia",
                      "Blue Island": "Illinois",
                      "West Bend": "Wisconsin",
                      "Alvin": "Texas",
                      "Culver City": "California",
                      "Hoboken": "New Jersey",
                      "Atascocita": "Texas",
                      "Ridgeland": "Mississippi",
                      "Wheaton": "Maryland",
                      "East Millcreek": "Utah",
                      "Ashwaubenon": "Wisconsin",
                      "West Lafayette": "Indiana",
                      "Worcester": "Massachusetts",
                      "Rocky River": "Ohio",
                      "Keystone": "Florida",
                      "Fayetteville": "Georgia",
                      "Laconia": "New Hampshire",
                      "Rosemont": "California",
                      "Spanish Springs": "Nevada",
                      "Fruit Cove": "Florida",
                      "Opelousas": "Louisiana",
                      "Jeffersontown": "Kentucky",
                      "Banning": "California",
                      "Lacey": "Washington",
                      "Oakdale": "Minnesota",
                      "Tucson": "Arizona",
                      "McDonough": "Georgia",
                      "Mahwah": "New Jersey",
                      "Providence": "Rhode Island",
                      "Rochester Hills": "Michigan",
                      "North Salt Lake": "Utah",
                      "Liberty": "Missouri",
                      "San Lorenzo": "California",
                      "Ludlow": "Massachusetts",
                      "Macon": "Georgia",
                      "Georgetown": "Texas",
                      "Schererville": "Indiana",
                      "Sikeston": "Missouri",
                      "Jamestown": "New York",
                      "Eau Claire": "Wisconsin",
                      "Lauderhill": "Florida",
                      "Metairie Terrace": "Louisiana",
                      "Fitchburg": "Wisconsin",
                      "Acton": "Massachusetts",
                      "Westerly": "Rhode Island",
                      "West Chester": "Pennsylvania",
                      "Denison": "Texas",
                      "Diamond Bar": "California",
                      "Goldsboro": "North Carolina",
                      "Chambersburg": "Pennsylvania",
                      "Merrick": "New York",
                      "Dolton": "Illinois",
                      "Hendersonville": "Tennessee",
                      "Vero Beach South": "Florida",
                      "Redford": "Michigan",
                      "Broomfield": "Colorado",
                      "Canoga Park": "California",
                      "Del City": "Oklahoma",
                      "Shorewood": "Illinois",
                      "Kingsport": "Tennessee",
                      "Akron": "Ohio",
                      "Ensley": "Florida",
                      "Mount Vernon": "New York",
                      "Piscataway": "New Jersey",
                      "Ellensburg": "Washington",
                      "Cahokia": "Illinois",
                      "Kissimmee": "Florida",
                      "Dothan": "Alabama",
                      "San Pablo": "California",
                      "Kahului": "Hawaii",
                      "Del Rio": "Texas",
                      "Alice": "Texas",
                      "Menlo Park": "California",
                      "South Salt Lake": "Utah",
                      "Broadview Heights": "Ohio",
                      "Chanhassen": "Minnesota",
                      "Haverhill": "Massachusetts",
                      "Tulsa": "Oklahoma",
                      "High Point": "North Carolina",
                      "San Rafael": "California",
                      "Clovis": "California",
                      "Ottawa": "Illinois",
                      "Des Plaines": "Illinois",
                      "Redland": "Maryland",
                      "West Orange": "New Jersey",
                      "South Vineland": "New Jersey",
                      "Baton Rouge": "Louisiana",
                      "Butte": "Montana",
                      "East Longmeadow": "Massachusetts",
                      "Los Banos": "California",
                      "Milwaukie": "Oregon",
                      "Santa Fe": "New Mexico",
                      "Chattanooga": "Tennessee",
                      "Spokane Valley": "Washington",
                      "Coachella": "California",
                      "Mission Viejo": "California",
                      "Severna Park": "Maryland",
                      "Algonquin": "Illinois",
                      "Green": "Ohio",
                      "Mehlville": "Missouri",
                      "Rancho Palos Verdes": "California",
                      "Carpentersville": "Illinois",
                      "Aurora": "Ohio",
                      "Dedham": "Massachusetts",
                      "Palmer": "Massachusetts",
                      "Eastlake": "Ohio",
                      "Syosset": "New York",
                      "Dixiana": "Alabama",
                      "East Setauket": "New York",
                      "Easthampton": "Massachusetts",
                      "Livonia": "Michigan",
                      "Silverdale": "Washington",
                      "Catonsville": "Maryland",
                      "Fountainebleau": "Florida",
                      "New Hope": "Minnesota",
                      "Seminole": "Florida",
                      "Town 'n' Country": "Florida",
                      "Corinth": "Texas",
                      "Lindenhurst": "New York",
                      "Liberal": "Kansas",
                      "Framingham Center": "Massachusetts",
                      "Pearl City": "Hawaii",
                      "Casa Grande": "Arizona",
                      "Mililani Town": "Hawaii",
                      "Ojus": "Florida",
                      "Kendale Lakes": "Florida",
                      "Fairbanks": "Alaska",
                      "Essex": "Maryland",
                      "Three Lakes": "Florida",
                      "Beverly Cove": "Massachusetts",
                      "Taylors": "South Carolina",
                      "Vestavia Hills": "Alabama",
                      "Salmon Creek": "Washington",
                      "Dix Hills": "New York",
                      "Alameda": "California",
                      "Mountain Brook": "Alabama",
                      "Sicklerville": "New Jersey",
                      "Groves": "Texas",
                      "East Chicago": "Indiana",
                      "Strongsville": "Ohio",
                      "Rotterdam": "New York",
                      "Plantation": "Florida",
                      "Bay City": "Michigan",
                      "West Raleigh": "North Carolina",
                      "Easton": "Massachusetts",
                      "Union City": "New Jersey",
                      "Nampa": "Idaho",
                      "Bartlesville": "Oklahoma",
                      "Norristown": "Pennsylvania",
                      "Jonesboro": "Arkansas",
                      "Waterloo": "Iowa",
                      "Lehi": "Utah",
                      "Holiday": "Florida",
                      "Mount Juliet": "Tennessee",
                      "Estelle": "Louisiana",
                      "Woodbury": "Minnesota",
                      "Belmont": "Massachusetts",
                      "Menifee": "California",
                      "Munster": "Indiana",
                      "Tracy": "California",
                      "Sheboygan": "Wisconsin",
                      "Wellington": "Florida",
                      "Bloomfield": "New Jersey",
                      "Addison": "Illinois",
                      "Tiffin": "Ohio",
                      "City of Sammamish": "Washington",
                      "Taylor": "Michigan",
                      "Bristol": "Rhode Island",
                      "Jasper": "Indiana",
                      "Saratoga Springs": "New York",
                      "Egypt Lake-Leto": "Florida",
                      "Fall River": "Massachusetts",
                      "Garland": "Texas",
                      "Sandy Hills": "Utah",
                      "Elkton": "Maryland",
                      "Harrison": "New York",
                      "Big Spring": "Texas",
                      "Coronado": "California",
                      "Rockville Centre": "New York",
                      "Roseburg": "Oregon",
                      "Perrysburg": "Ohio",
                      "Miami Beach": "Florida",
                      "Scranton": "Pennsylvania",
                      "Centralia": "Washington",
                      "Muskogee": "Oklahoma",
                      "Edina": "Minnesota",
                      "North Aurora": "Illinois",
                      "Smyrna": "Georgia",
                      "Omaha": "Nebraska",
                      "Avon": "Ohio",
                      "Clarksdale": "Mississippi",
                      "Sandusky": "Ohio",
                      "Hazel Park": "Michigan",
                      "Tempe": "Arizona",
                      "West Covina": "California",
                      "Grandville": "Michigan",
                      "Pahrump": "Nevada",
                      "Temple Terrace": "Florida",
                      "Norton": "Massachusetts",
                      "Dinuba": "California",
                      "Kirksville": "Missouri",
                      "Fuquay-Varina": "North Carolina",
                      "Oxnard": "California",
                      "Apopka": "Florida",
                      "New Albany": "Indiana",
                      "Old Bridge": "New Jersey",
                      "Stoneham": "Massachusetts",
                      "Jenison": "Michigan",
                      "West Hills": "California",
                      "Annapolis": "Maryland",
                      "Jefferson City": "Missouri",
                      "Southaven": "Mississippi",
                      "Chaska": "Minnesota",
                      "Appleton": "Wisconsin",
                      "Ansonia": "Connecticut",
                      "Hopatcong Hills": "New Jersey",
                      "Cimarron Hills": "Colorado",
                      "Orinda": "California",
                      "New Castle": "Pennsylvania",
                      "Altamont": "Oregon",
                      "Noblesville": "Indiana",
                      "Edmonds": "Washington",
                      "Irvington": "New Jersey",
                      "Mount Clemens": "Michigan",
                      "Knoxville": "Tennessee",
                      "Longmeadow": "Massachusetts",
                      "Harrisburg": "Pennsylvania",
                      "Hutchinson": "Kansas",
                      "Saint Clair Shores": "Michigan",
                      "San Carlos": "California",
                      "Tustin": "California",
                      "Claremont": "California",
                      "Immokalee": "Florida",
                      "West Des Moines": "Iowa",
                      "Lehigh Acres": "Florida",
                      "East Hill-Meridian": "Washington",
                      "Gadsden": "Alabama",
                      "Orcutt": "California",
                      "Plainfield": "Illinois",
                      "San Leandro": "California",
                      "New Philadelphia": "Ohio",
                      "Broken Arrow": "Oklahoma",
                      "Ada": "Oklahoma",
                      "Oakland Park": "Florida",
                      "Palmdale": "California",
                      "Fairfield Heights": "Indiana",
                      "Central Islip": "New York",
                      "Cathedral City": "California",
                      "Sunset": "Florida",
                      "Nogales": "Arizona",
                      "Jenks": "Oklahoma",
                      "Oildale": "California",
                      "Kent": "Washington",
                      "Fridley": "Minnesota",
                      "Cudahy": "Wisconsin",
                      "Whitehall Township": "Pennsylvania",
                      "Lawrence": "Massachusetts",
                      "Oshkosh": "Wisconsin",
                      "San Bruno": "California",
                      "Dalton": "Georgia",
                      "Lake in the Hills": "Illinois",
                      "Honolulu": "Hawaii",
                      "Iselin": "New Jersey",
                      "Sandy Springs": "Georgia",
                      "Mastic": "New York",
                      "Frederickson": "Washington",
                      "Westland": "Michigan",
                      "Oxon Hill": "Maryland",
                      "Asbury Park": "New Jersey",
                      "Cranberry Township": "Pennsylvania",
                      "Antioch": "California",
                      "Central Point": "Oregon",
                      "South Burlington": "Vermont",
                      "Sammamish": "Washington",
                      "Catalina Foothills": "Arizona",
                      "Oak Lawn": "Illinois",
                      "Central": "Louisiana",
                      "Damascus": "Maryland",
                      "Kokomo": "Indiana",
                      "Santa Ana": "California",
                      "Louisville": "Colorado",
                      "Clermont": "Florida",
                      "Framingham": "Massachusetts",
                      "East Chattanooga": "Tennessee",
                      "Olathe": "Kansas",
                      "South Bel Air": "Maryland",
                      "Franklin Park": "Illinois",
                      "Newburgh": "New York",
                      "South Yuba City": "California",
                      "Morton Grove": "Illinois",
                      "Socastee": "South Carolina",
                      "Fort Bragg": "North Carolina",
                      "Kendall": "Florida",
                      "Hopatcong": "New Jersey",
                      "Valley Station": "Kentucky",
                      "Beavercreek": "Ohio",
                      "South Hill": "Washington",
                      "Massapequa Park": "New York",
                      "El Segundo": "California",
                      "Pasco": "Washington",
                      "Norwood": "Ohio",
                      "Brookings": "South Dakota",
                      "Fernley": "Nevada",
                      "West Jordan": "Utah",
                      "Novi": "Michigan",
                      "Caledonia": "Wisconsin",
                      "North Bay Shore": "New York",
                      "Twinsburg": "Ohio",
                      "Biloxi": "Mississippi",
                      "Albert Lea": "Minnesota",
                      "Machesney Park": "Illinois",
                      "Clifton": "New Jersey",
                      "North Lauderdale": "Florida",
                      "Merrimack": "New Hampshire",
                      "Kearny": "New Jersey",
                      "Arcata": "California",
                      "East Lake": "Florida",
                      "Hope Mills": "North Carolina",
                      "Woodbridge": "New Jersey",
                      "Suitland": "Maryland",
                      "Janesville": "Wisconsin",
                      "Phoenix": "Arizona",
                      "West Fargo": "North Dakota",
                      "Lumberton": "North Carolina",
                      "Libertyville": "Illinois",
                      "Grand Island": "Nebraska",
                      "McKeesport": "Pennsylvania",
                      "Elko": "Nevada",
                      "Portage": "Indiana",
                      "Folsom": "California",
                      "Langley Park": "Maryland",
                      "Massillon": "Ohio",
                      "Waverly": "Michigan",
                      "Eagle": "Idaho",
                      "Warren Township": "New Jersey",
                      "Meridian": "Idaho",
                      "Chelmsford": "Massachusetts",
                      "Yakima": "Washington",
                      "Longmont": "Colorado",
                      "White Plains": "New York",
                      "Saginaw": "Michigan",
                      "Silver Spring": "Maryland",
                      "North Bergen": "New Jersey",
                      "Cedar Park": "Texas",
                      "SeaTac": "Washington",
                      "Placentia": "California",
                      "Davis": "California",
                      "Douglas": "Arizona",
                      "Snellville": "Georgia",
                      "Farmington Hills": "Michigan",
                      "Evans": "Georgia",
                      "West Milford": "New Jersey",
                      "St. Louis": "Missouri",
                      "Prunedale": "California",
                      "Milwaukee": "Wisconsin",
                      "Westlake": "Ohio",
                      "Depew": "New York",
                      "Friendswood": "Texas",
                      "Johnstown": "Pennsylvania",
                      "Mount Pleasant": "Michigan",
                      "Las Cruces": "New Mexico",
                      "Lakeville": "Minnesota",
                      "Manhattan Beach": "California",
                      "Opportunity": "Washington",
                      "Gurnee": "Illinois",
                      "North Charleston": "South Carolina",
                      "Soledad": "California",
                      "Thomasville": "North Carolina",
                      "Riverview": "Florida",
                      "Canon City": "Colorado",
                      "Truckee": "California",
                      "Lockport": "New York",
                      "Columbia": "Maryland",
                      "Rockledge": "Florida",
                      "Wildwood": "Missouri",
                      "Glen Cove": "New York",
                      "Lynn": "Massachusetts",
                      "Wisconsin Rapids": "Wisconsin",
                      "Owatonna": "Minnesota",
                      "Arcadia": "California",
                      "San Ramon": "California",
                      "North Providence": "Rhode Island",
                      "Owasso": "Oklahoma",
                      "Santa Cruz": "California",
                      "Goodlettsville": "Tennessee",
                      "Moore": "Oklahoma",
                      "Winter Haven": "Florida",
                      "Red Wing": "Minnesota",
                      "Northbrook": "Illinois",
                      "Hermiston": "Oregon",
                      "Reedley": "California",
                      "Candler-McAfee": "Georgia",
                      "South San Francisco": "California",
                      "Fort Wayne": "Indiana",
                      "Simi Valley": "California",
                      "Bridgeton": "New Jersey",
                      "Iowa City": "Iowa",
                      "Lochearn": "Maryland",
                      "Atlantic City": "New Jersey",
                      "Beacon": "New York",
                      "Camas": "Washington",
                      "Mankato": "Minnesota",
                      "Martha Lake": "Washington",
                      "Lakeside": "Florida",
                      "Glenview": "Illinois",
                      "Greater Northdale": "Florida",
                      "Klamath Falls": "Oregon",
                      "Golden Glades": "Florida",
                      "Hazel Dell": "Washington",
                      "Okemos": "Michigan",
                      "Galesburg": "Illinois",
                      "Greeneville": "Tennessee",
                      "Horn Lake": "Mississippi",
                      "Auburn": "Massachusetts",
                      "Kentwood": "Michigan",
                      "Pampa": "Texas",
                      "Gainesville": "Texas",
                      "King of Prussia": "Pennsylvania",
                      "East Riverdale": "Maryland",
                      "Edwardsville": "Illinois",
                      "Anchorage": "Alaska",
                      "Oak Hill": "Virginia",
                      "Fort Myers": "Florida",
                      "Moses Lake": "Washington",
                      "Grafton": "Massachusetts",
                      "Westminster": "Maryland",
                      "Springfield": "Massachusetts",
                      "Pickerington": "Ohio",
                      "New Bedford": "Massachusetts",
                      "Moorpark": "California",
                      "City of Milford (balance)": "Connecticut",
                      "Evergreen Park": "Illinois",
                      "Dayton": "Ohio",
                      "Pleasure Ridge Park": "Kentucky",
                      "Holbrook": "New York",
                      "Holland": "Michigan",
                      "Sidney": "Ohio",
                      "West Odessa": "Texas",
                      "Secaucus": "New Jersey",
                      "Jupiter": "Florida",
                      "Johnson City": "Tennessee",
                      "Gulfport": "Mississippi",
                      "Ardmore": "Oklahoma",
                      "Minnetonka Mills": "Minnesota",
                      "Myrtle Beach": "South Carolina",
                      "Sahuarita": "Arizona",
                      "Palm Springs": "California",
                      "Pelham": "Alabama",
                      "Ontario": "California",
                      "Ham Lake": "Minnesota",
                      "Birmingham": "Alabama",
                      "Upper Arlington": "Ohio",
                      "North Ridgeville": "Ohio",
                      "Marietta": "Georgia",
                      "Wakefield": "Massachusetts",
                      "Imperial Beach": "California",
                      "Huntsville": "Alabama",
                      "Pico Rivera": "California",
                      "Pearl": "Mississippi",
                      "Cameron Park": "California",
                      "Ankeny": "Iowa",
                      "Lompoc": "California",
                      "Okolona": "Kentucky",
                      "Maywood": "Illinois",
                      "Loves Park": "Illinois",
                      "Martinez": "California",
                      "Norland": "Florida",
                      "Cranford": "New Jersey",
                      "Lansdale": "Pennsylvania",
                      "Shoreview": "Minnesota",
                      "Independence": "Kentucky",
                      "Orange": "New Jersey",
                      "Hudson": "Ohio",
                      "Stuart": "Florida",
                      "Woodridge": "Illinois",
                      "Suisun": "California",
                      "Cherry Hill": "New Jersey",
                      "Inver Grove Heights": "Minnesota",
                      "Highland Park": "Illinois",
                      "Gloucester": "Massachusetts",
                      "Elkridge": "Maryland",
                      "Brooklyn": "New York",
                      "Teaneck": "New Jersey",
                      "Wolcott": "Connecticut",
                      "Vero Beach": "Florida",
                      "Lynwood": "California",
                      "Redding": "California",
                      "East Pensacola Heights": "Florida",
                      "Cheektowaga": "New York",
                      "Oakville": "Missouri",
                      "Broad Ripple": "Indiana",
                      "Grand Junction": "Colorado",
                      "Oswego": "New York",
                      "Terre Haute": "Indiana",
                      "Glen Avon": "California",
                      "Bullhead City": "Arizona",
                      "Monsey": "New York",
                      "Delray Beach": "Florida",
                      "Manitowoc": "Wisconsin",
                      "Drexel Heights": "Arizona",
                      "Frederick": "Maryland",
                      "Rock Springs": "Wyoming",
                      "Pottstown": "Pennsylvania",
                      "Key West": "Florida",
                      "Sayville": "New York",
                      "Leominster": "Massachusetts",
                      "Riviera Beach": "Florida",
                      "Howard": "Wisconsin",
                      "Highland": "Indiana",
                      "Englewood": "New Jersey",
                      "Socorro": "Texas",
                      "Bayonne": "New Jersey",
                      "West Springfield": "Massachusetts",
                      "Bear": "Delaware",
                      "Bessemer": "Alabama",
                      "Holt": "Michigan",
                      "Issaquah": "Washington",
                      "Newburyport": "Massachusetts",
                      "Bolingbrook": "Illinois",
                      "Raytown": "Missouri",
                      "New Brighton": "Minnesota",
                      "West Whittier-Los Nietos": "California",
                      "Murray": "Kentucky",
                      "Elmont": "New York",
                      "Odessa": "Texas",
                      "Burleson": "Texas",
                      "Paradise": "California",
                      "Petaluma": "California",
                      "Brawley": "California",
                      "Maple Valley": "Washington",
                      "Brooklyn Center": "Minnesota",
                      "Delaware": "Ohio",
                      "Zanesville": "Ohio",
                      "Prior Lake": "Minnesota",
                      "Union": "New Jersey",
                      "Hastings": "Nebraska",
                      "Fountain Hills": "Arizona",
                      "Greenfield": "Wisconsin",
                      "Rosemead": "California",
                      "Altoona": "Pennsylvania",
                      "Millbrae": "California",
                      "Bangor": "Maine",
                      "Shelby": "Michigan",
                      "Pleasant Prairie": "Wisconsin",
                      "Spring Hill": "Florida",
                      "Central Falls": "Rhode Island",
                      "Perth Amboy": "New Jersey",
                      "Hackensack": "New Jersey",
                      "Boynton Beach": "Florida",
                      "North Hollywood": "California",
                      "Greenacres City": "Florida",
                      "Garfield": "New Jersey",
                      "Hilton Head Island": "South Carolina",
                      "South Portland Gardens": "Maine",
                      "Bel Air North": "Maryland",
                      "Morrisville": "North Carolina",
                      "Silver Firs": "Washington",
                      "Bonney Lake": "Washington",
                      "Brentwood": "California",
                      "Saint Paul": "Minnesota",
                      "Coeur d'Alene": "Idaho",
                      "Potomac": "Maryland",
                      "Hollister": "California",
                      "Pleasant Hill": "California",
                      "Land O' Lakes": "Florida",
                      "Palm Beach Gardens": "Florida",
                      "Brookhaven": "Georgia",
                      "Hallandale Beach": "Florida",
                      "Champlin": "Minnesota",
                      "East Hemet": "California",
                      "Piqua": "Ohio",
                      "Carrollwood": "Florida",
                      "Helena": "Montana",
                      "Mint Hill": "North Carolina",
                      "San Angelo": "Texas",
                      "Montrose": "Colorado",
                      "Mountain Top": "Pennsylvania",
                      "New Bern": "North Carolina",
                      "Dickinson": "North Dakota",
                      "West and East Lealman": "Florida",
                      "Haslett": "Michigan",
                      "Dublin": "California",
                      "South Ogden": "Utah",
                      "Rancho Cucamonga": "California",
                      "Castle Rock": "Colorado",
                      "Winter Garden": "Florida",
                      "Steubenville": "Ohio",
                      "Greenbelt": "Maryland",
                      "Chicopee": "Massachusetts",
                      "Monrovia": "California",
                      "Hanford": "California",
                      "Plymouth": "Minnesota",
                      "Shafter": "California",
                      "Iron River": "Michigan",
                      "Eustis": "Florida",
                      "Hillside": "New Jersey",
                      "Urbandale": "Iowa",
                      "Wright": "Florida",
                      "Scarsdale": "New York",
                      "Green Haven": "Maryland",
                      "Anthem": "Arizona",
                      "Tempe Junction": "Arizona",
                      "San Fernando": "California",
                      "Davie": "Florida",
                      "Punta Gorda": "Florida",
                      "Ferry Pass": "Florida",
                      "Lincoln": "Nebraska",
                      "Lakeland": "Florida",
                      "Park Ridge": "Illinois",
                      "Midwest City": "Oklahoma",
                      "Shirley": "New York",
                      "Allentown": "Pennsylvania",
                      "Collierville": "Tennessee",
                      "El Mirage": "Arizona",
                      "Muskegon": "Michigan",
                      "El Paso": "Texas",
                      "Carson City": "Nevada",
                      "Muscatine": "Iowa",
                      "University City": "Missouri",
                      "Moraga": "California",
                      "Painesville": "Ohio",
                      "East Meadow": "New York",
                      "Cupertino": "California",
                      "American Canyon": "California",
                      "Wyandotte": "Michigan",
                      "Pullman": "Washington",
                      "Fort Dodge": "Iowa",
                      "Prichard": "Alabama",
                      "Hazelwood": "Missouri",
                      "North Little Rock": "Arkansas",
                      "Lake Butler": "Florida",
                      "Tinley Park": "Illinois",
                      "Gallatin": "Tennessee",
                      "Sherwood": "Oregon",
                      "Lodi": "New Jersey",
                      "Kankakee": "Illinois",
                      "Drexel Hill": "Pennsylvania",
                      "Sartell": "Minnesota",
                      "Lewiston": "Maine",
                      "Conway": "Arkansas",
                      "Tifton": "Georgia",
                      "Tacoma": "Washington",
                      "Milton": "Massachusetts",
                      "Saint Michael": "Minnesota",
                      "Philadelphia": "Pennsylvania",
                      "North Amityville": "New York",
                      "Copperas Cove": "Texas",
                      "North Peoria": "Illinois",
                      "Little Rock": "Arkansas",
                      "Poway": "California",
                      "Brushy Creek": "Texas",
                      "Wheat Ridge": "Colorado",
                      "Cantonment": "Florida",
                      "New Brunswick": "New Jersey",
                      "Chillum": "Maryland",
                      "Mundelein": "Illinois",
                      "Nicholasville": "Kentucky",
                      "Kiryas Joel": "New York",
                      "Huntington Park": "California",
                      "Maple Shade": "New Jersey",
                      "Charlotte": "North Carolina",
                      "Phoenixville": "Pennsylvania",
                      "Sunnyside": "Washington",
                      "Boulder": "Colorado",
                      "Ashtabula": "Ohio",
                      "Glassboro": "New Jersey",
                      "Danvers": "Massachusetts",
                      "Mason City": "Iowa",
                      "Abilene": "Texas",
                      "Anoka": "Minnesota",
                      "Lisle": "Illinois",
                      "Cabot": "Arkansas",
                      "Walnut Park": "California",
                      "Bayou Cane": "Louisiana",
                      "Winthrop": "Massachusetts",
                      "Salinas": "California",
                      "Manchester": "New Hampshire",
                      "Lawrenceville": "Georgia",
                      "Southbridge": "Massachusetts",
                      "Alafaya": "Florida",
                      "Brigham City": "Utah",
                      "Redwood City": "California",
                      "Plattsburgh": "New York",
                      "Olympia": "Washington",
                      "Glendora": "California",
                      "Willmar": "Minnesota",
                      "Walla Walla": "Washington",
                      "Saugus": "Massachusetts",
                      "Parma Heights": "Ohio",
                      "Searcy": "Arkansas",
                      "Long Beach": "California",
                      "Whittier": "California",
                      "Buffalo Grove": "Illinois",
                      "Highview": "Kentucky",
                      "San Pedro": "California",
                      "Bloomington": "Indiana",
                      "Santa Rosa": "California",
                      "Adelphi": "Maryland",
                      "Pinole": "California",
                      "Pasadena": "California",
                      "Floral Park": "New York",
                      "Roselle": "Illinois",
                      "Wilsonville": "Oregon",
                      "Carmichael": "California",
                      "Burlington": "Kentucky",
                      "Salisbury": "Maryland",
                      "Van Buren": "Arkansas",
                      "Attleboro": "Massachusetts",
                      "Hinsdale": "Illinois",
                      "Stillwater": "Oklahoma",
                      "Maryland City": "Maryland",
                      "Milford": "Massachusetts",
                      "Greenburgh": "New York",
                      "Kaukauna": "Wisconsin",
                      "Scottsbluff": "Nebraska",
                      "Midvale": "Utah",
                      "Canby": "Oregon",
                      "Binghamton": "New York",
                      "Burien": "Washington",
                      "Florence-Graham": "California",
                      "Mentor": "Ohio",
                      "Lakewood": "Washington",
                      "Oak Park": "Michigan",
                      "Fullerton": "California",
                      "Citrus Heights": "California",
                      "Westerville": "Ohio",
                      "Seymour": "Indiana",
                      "Pueblo": "Colorado",
                      "Fair Oaks": "California",
                      "Milford Mill": "Maryland",
                      "Corvallis": "Oregon",
                      "Bartlett": "Illinois",
                      "Deerfield Beach": "Florida",
                      "East Lansing": "Michigan",
                      "Sycamore": "Illinois",
                      "Colchester": "Vermont",
                      "Middletown": "Rhode Island",
                      "Washington, D.C.": "District of Columbia",
                      "South Gate": "California",
                      "Medford": "Oregon",
                      "Oak Harbor": "Washington",
                      "Jacksonville": "Arkansas",
                      "Alpharetta": "Georgia",
                      "Artesia": "California",
                      "Franklin": "Massachusetts",
                      "Rubidoux": "California",
                      "Reading": "Massachusetts",
                      "Wyoming": "Michigan",
                      "Marblehead": "Massachusetts",
                      "South Laurel": "Maryland",
                      "Fords": "New Jersey",
                      "Woodland Hills": "California",
                      "Amsterdam": "New York",
                      "Saint George": "Utah",
                      "Pace": "Florida",
                      "Lemay": "Missouri",
                      "Roy": "Utah",
                      "Bellaire": "Texas",
                      "Gallup": "New Mexico",
                      "San Mateo": "California",
                      "Hanover Park": "Illinois",
                      "Bowling Green": "Ohio",
                      "East Palo Alto": "California",
                      "Puyallup": "Washington",
                      "Eden": "North Carolina",
                      "Orangevale": "California",
                      "Coon Rapids": "Minnesota",
                      "Baltimore": "Maryland",
                      "South Pasadena": "California",
                      "West Palm Beach": "Florida",
                      "San Juan Capistrano": "California",
                      "Pleasantville": "New Jersey",
                      "Pleasanton": "California",
                      "Wildomar": "California",
                      "Whitney": "Nevada",
                      "Ozark": "Missouri",
                      "Iona": "Florida",
                      "Boston": "Massachusetts",
                      "Salem": "Oregon",
                      "Lemont": "Illinois",
                      "Carteret": "New Jersey",
                      "Bellevue": "Nebraska",
                      "Waldorf": "Maryland",
                      "Grand Rapids": "Michigan",
                      "Golden Valley": "Minnesota",
                      "Streetsboro": "Ohio",
                      "Schenectady": "New York",
                      "Kettering": "Ohio",
                      "Huntersville": "North Carolina",
                      "Arlington": "Washington",
                      "Beverly Hills": "California",
                      "Beloit": "Wisconsin",
                      "Arvada": "Colorado",
                      "Paramus": "New Jersey",
                      "Minneapolis": "Minnesota",
                      "Country Walk": "Florida",
                      "Tallmadge": "Ohio",
                      "Clearfield": "Utah",
                      "Jamaica": "New York",
                      "Rockford": "Illinois",
                      "Redondo Beach": "California",
                      "Cottage Grove": "Minnesota",
                      "Agoura Hills": "California",
                      "Stanton": "California",
                      "Smithfield": "Rhode Island",
                      "Bixby": "Oklahoma",
                      "Fort Pierce": "Florida",
                      "Adrian": "Michigan",
                      "Bay Point": "California",
                      "Renton": "Washington",
                      "Erie": "Colorado",
                      "Rolling Meadows": "Illinois",
                      "Sparks": "Nevada",
                      "West Albany": "New York",
                      "North Las Vegas": "Nevada",
                      "Atlanta": "Georgia",
                      "Redmond": "Washington",
                      "Passaic": "New Jersey",
                      "Westbrook": "Maine",
                      "Gladstone": "Missouri",
                      "Willimantic": "Connecticut",
                      "Clemmons": "North Carolina",
                      "Woodlawn": "Maryland",
                      "Citrus Park": "Florida",
                      "Compton": "California",
                      "Enid": "Oklahoma",
                      "North Valley Stream": "New York",
                      "Farmington": "Utah",
                      "Alliance": "Ohio",
                      "Twin Falls": "Idaho",
                      "Neenah": "Wisconsin",
                      "Santa Barbara": "California",
                      "Winter Gardens": "California",
                      "Windham": "Connecticut",
                      "Westport": "Connecticut",
                      "Bloomingdale": "Florida",
                      "Romulus": "Michigan",
                      "Donna": "Texas",
                      "Fair Lawn": "New Jersey",
                      "Utica": "New York",
                      "Sierra Vista": "Arizona",
                      "South Plainfield": "New Jersey",
                      "Rogers": "Arkansas",
                      "Seaford": "New York",
                      "Sherrelwood": "Colorado",
                      "Mattoon": "Illinois",
                      "Warren": "Ohio",
                      "Coventry": "Rhode Island",
                      "Billings": "Montana",
                      "Miramar": "Florida",
                      "Carson": "California",
                      "Ukiah": "California",
                      "Ames": "Iowa",
                      "Watsonville": "California",
                      "Richland": "Washington",
                      "Coral Gables": "Florida",
                      "Hot Springs National Park": "Arkansas",
                      "Bainbridge Island": "Washington",
                      "Battle Ground": "Washington",
                      "Lake Worth": "Florida",
                      "Colorado Springs": "Colorado",
                      "Daytona Beach": "Florida",
                      "Forest Hills": "Michigan",
                      "Setauket-East Setauket": "New York",
                      "Salina": "Kansas",
                      "Manteca": "California",
                      "Sandy City": "Utah",
                      "Upper Alton": "Illinois",
                      "Grosse Pointe Woods": "Michigan",
                      "Forest Grove": "Oregon",
                      "Savannah": "Georgia",
                      "Flagami": "Florida",
                      "Kearney": "Nebraska",
                      "Grandview": "Missouri",
                      "Williamsport": "Pennsylvania",
                      "Port Angeles": "Washington",
                      "Coconut Grove": "Florida",
                      "Boone": "North Carolina",
                      "Cheyenne": "Wyoming",
                      "North Bel Air": "Maryland",
                      "South Boston": "Massachusetts",
                      "Logansport": "Indiana",
                      "Flagstaff": "Arizona",
                      "Thousand Oaks": "California",
                      "Roanoke Rapids": "North Carolina",
                      "Takoma Park": "Maryland",
                      "Statesville": "North Carolina",
                      "Palm City": "Florida",
                      "East Orange": "New Jersey",
                      "Waterford": "Michigan",
                      "Maple Grove": "Minnesota",
                      "Metairie": "Louisiana",
                      "Alton": "Illinois",
                      "Commack": "New York",
                      "Rancho Santa Margarita": "California",
                      "East Massapequa": "New York",
                      "Wahiawa": "Hawaii",
                      "Gatesville": "Texas",
                      "Romeoville": "Illinois",
                      "Peoria": "Arizona",
                      "Tumwater": "Washington",
                      "North Fort Myers": "Florida",
                      "Overland": "Missouri",
                      "Monroeville": "Pennsylvania",
                      "Holladay": "Utah",
                      "Palo Alto": "California",
                      "Meads": "Kentucky",
                      "North Chicago": "Illinois",
                      "Marshfield": "Wisconsin",
                      "Clearlake": "California",
                      "Napa": "California",
                      "Hamilton": "Ohio",
                      "Corsicana": "Texas",
                      "North Miami": "Florida",
                      "Franklin Square": "New York",
                      "Rocklin": "California",
                      "Germantown": "Tennessee",
                      "Weirton Heights": "West Virginia",
                      "Irvine": "California",
                      "Oviedo": "Florida",
                      "Summerlin South": "Nevada",
                      "Redlands": "California",
                      "Miamisburg": "Ohio",
                      "Oregon": "Ohio",
                      "Simpsonville": "South Carolina",
                      "Belleville": "Illinois",
                      "Waterville": "Maine",
                      "Zion": "Illinois",
                      "Anderson": "South Carolina",
                      "Oconomowoc": "Wisconsin",
                      "Twentynine Palms": "California",
                      "South Orange": "New Jersey",
                      "Los Angeles": "California",
                      "Clive": "Iowa",
                      "Fairborn": "Ohio",
                      "Linden": "New Jersey",
                      "San Luis Obispo": "California",
                      "Natchez": "Mississippi",
                      "Cutler": "Florida",
                      "Wilkes-Barre": "Pennsylvania",
                      "Cottonwood Heights": "Utah",
                      "Palisades Park": "New Jersey",
                      "Springdale": "Arkansas",
                      "Waltham": "Massachusetts",
                      "East Point": "Georgia",
                      "Yorkville": "Illinois",
                      "Lindenwold": "New Jersey",
                      "El Dorado Hills": "California",
                      "Trenton": "Michigan",
                      "Pomona": "California",
                      "Castlewood": "Colorado",
                      "Springville": "Utah",
                      "North Massapequa": "New York",
                      "Yucca Valley": "California",
                      "Port Saint Lucie": "Florida",
                      "Boyle Heights": "California",
                      "Elmhurst": "Illinois",
                      "Sapulpa": "Oklahoma",
                      "Durango": "Colorado",
                      "Eugene": "Oregon",
                      "Prospect Heights": "Illinois",
                      "Orlando": "Florida",
                      "Lents": "Oregon",
                      "Maricopa": "Arizona",
                      "Saco": "Maine",
                      "Asheboro": "North Carolina",
                      "Alsip": "Illinois",
                      "Medina": "Ohio",
                      "Vancouver": "Washington",
                      "Lake Ronkonkoma": "New York",
                      "Coralville": "Iowa",
                      "Kirkwood": "Missouri",
                      "Joliet": "Illinois",
                      "Austintown": "Ohio",
                      "Chino Hills": "California",
                      "Carrollwood Village": "Florida",
                      "West Pensacola": "Florida",
                      "Coney Island": "New York",
                      "Eagle River": "Alaska",
                      "Costa Mesa": "California",
                      "Back Mountain": "Pennsylvania",
                      "Colton": "California",
                      "Wayne": "New Jersey",
                      "Muskego": "Wisconsin",
                      "Hopkins": "Minnesota",
                      "Greenwood": "South Carolina",
                      "Duluth": "Minnesota",
                      "Amherst Center": "Massachusetts",
                      "Pontiac": "Michigan",
                      "West Saint Paul": "Minnesota",
                      "Union Hill-Novelty Hill": "Washington",
                      "Middleton": "Wisconsin",
                      "Holden": "Massachusetts",
                      "Woonsocket": "Rhode Island",
                      "Houston": "Texas",
                      "Pittsburgh": "Pennsylvania",
                      "Berkeley": "California",
                      "Barstow Heights": "California",
                      "Rialto": "California",
                      "Arlington Heights": "Illinois",
                      "Melville": "New York",
                      "Bellwood": "Illinois",
                      "Cutler Ridge": "Florida",
                      "Pawtucket": "Rhode Island",
                      "Farmingville": "New York",
                      "Willowbrook": "California",
                      "Enterprise": "Nevada",
                      "El Monte": "California",
                      "Glen Ellyn": "Illinois",
                      "Haines City": "Florida",
                      "Wade Hampton": "South Carolina",
                      "College Station": "Texas",
                      "Tuscaloosa": "Alabama",
                      "Cape Coral": "Florida",
                      "DeSoto": "Texas",
                      "North Decatur": "Georgia",
                      "Bridgeview": "Illinois",
                      "Decatur": "Georgia",
                      "Darien": "Illinois",
                      "Gary": "Indiana",
                      "Laramie": "Wyoming",
                      "Santa Paula": "California",
                      "Grayslake": "Illinois",
                      "Enchanted Hills": "New Mexico",
                      "Wilson": "North Carolina",
                      "Miami Lakes": "Florida",
                      "Brookfield": "Wisconsin",
                      "Plum": "Pennsylvania",
                      "Adelanto": "California",
                      "Harvey": "Louisiana",
                      "Bellview": "Florida",
                      "Clearwater": "Florida",
                      "Parma": "Ohio",
                      "Farragut": "Tennessee",
                      "Saint Joseph": "Missouri",
                      "Norton Shores": "Michigan",
                      "Crystal": "Minnesota",
                      "Montebello": "California",
                      "South Saint Paul": "Minnesota",
                      "Ann Arbor": "Michigan",
                      "Plant City": "Florida",
                      "Dana Point": "California",
                      "Cinco Ranch": "Texas",
                      "Centennial": "Colorado",
                      "Monterey": "California",
                      "Lexington": "Kentucky",
                      "Chula Vista": "California",
                      "Bettendorf": "Iowa",
                      "Gaithersburg": "Maryland",
                      "Ogden": "Utah",
                      "Prescott Valley": "Arizona",
                      "Blue Springs": "Missouri",
                      "Brooklyn Park": "Minnesota",
                      "Pacifica": "California",
                      "South Milwaukee": "Wisconsin",
                      "Owensboro": "Kentucky",
                      "Myrtle Grove": "Florida",
                      "West Chicago": "Illinois",
                      "Hobbs": "New Mexico",
                      "Grand Prairie": "Texas",
                      "Wesley Chapel": "Florida",
                      "La Vista": "Nebraska",
                      "Punta Gorda Isles": "Florida",
                      "Westford": "Massachusetts",
                      "Boca Del Mar": "Florida",
                      "Horizon City": "Texas",
                      "Ashland": "Massachusetts",
                      "Ocean Springs": "Mississippi",
                      "Pine Hills": "Florida",
                      "Uniondale": "New York",
                      "Oregon City": "Oregon",
                      "Fillmore": "California",
                      "Wailuku": "Hawaii",
                      "Wadsworth": "Ohio",
                      "Forest Lake": "Minnesota",
                      "San Carlos Park": "Florida",
                      "North Chicopee": "Massachusetts",
                      "Phenix City": "Alabama",
                      "Opelika": "Alabama",
                      "Round Lake": "Illinois",
                      "Bellingham": "Washington",
                      "Eastchester": "New York",
                      "Barnstable": "Massachusetts",
                      "Newton": "Kansas",
                      "Granite City": "Illinois",
                      "Buena Park": "California",
                      "Sayreville Junction": "New Jersey",
                      "Beaver Dam": "Wisconsin",
                      "Yorba Linda": "California",
                      "Rancho San Diego": "California",
                      "Hayesville": "Oregon",
                      "Burlingame": "California",
                      "Inglewood-Finn Hill": "Washington",
                      "Bayshore Gardens": "Florida",
                      "Camden": "New Jersey",
                      "Allison Park": "Pennsylvania",
                      "Port Hueneme": "California",
                      "West Hollywood": "California",
                      "Leavenworth": "Kansas",
                      "Lake Charles": "Louisiana",
                      "Westchase": "Florida",
                      "Glassmanor": "Maryland",
                      "Arden-Arcade": "California",
                      "Azusa": "California",
                      "Fontana": "California",
                      "North Arlington": "New Jersey",
                      "East Moline": "Illinois",
                      "Ithaca": "New York",
                      "Lutz": "Florida",
                      "West Melbourne": "Florida",
                      "East Peoria": "Illinois",
                      "Bourbonnais": "Illinois",
                      "Badger": "Alaska",
                      "North Ogden": "Utah",
                      "Columbine": "Colorado",
                      "Sebastian": "Florida",
                      "East Lake-Orient Park": "Florida",
                      "Morganton": "North Carolina",
                      "Bayside": "California",
                      "Sunrise": "Florida",
                      "Atascadero": "California",
                      "Athens": "Georgia",
                      "Batavia": "Illinois",
                      "Layton": "Utah",
                      "Hueytown": "Alabama",
                      "Benbrook": "Texas",
                      "Mansfield": "Ohio",
                      "Hempstead": "New York",
                      "Menomonie": "Wisconsin",
                      "Reynoldsburg": "Ohio",
                      "Northampton": "Massachusetts",
                      "Asheville": "North Carolina",
                      "Seal Beach": "California",
                      "Dixon": "Illinois",
                      "Butte-Silver Bow (Balance)": "Montana",
                      "Bradley": "Illinois",
                      "Melbourne": "Florida",
                      "Mesa": "Arizona",
                      "Pooler": "Georgia",
                      "Carlisle": "Pennsylvania",
                      "Easley": "South Carolina",
                      "East Los Angeles": "California",
                      "Aventura": "Florida",
                      "Cypress": "California",
                      "Ramona": "California",
                      "Palm Bay": "Florida",
                      "Avondale": "Arizona",
                      "Kingsland": "Georgia",
                      "Sugar Hill": "Georgia",
                      "Galveston": "Texas",
                      "Dyersburg": "Tennessee",
                      "Bethpage": "New York",
                      "Canton": "Georgia",
                      "Altadena": "California",
                      "Randolph": "Massachusetts",
                      "Rutland": "Vermont",
                      "West Sacramento": "California",
                      "Toledo": "Ohio",
                      "Elkhart": "Indiana",
                      "Elk Grove Village": "Illinois",
                      "Malden": "Massachusetts",
                      "Lima": "Ohio",
                      "Shakopee": "Minnesota",
                      "Mayfield Heights": "Ohio",
                      "Willow Grove": "Pennsylvania",
                      "Ironville": "Kentucky",
                      "Arvin": "California",
                      "Bryant": "Arkansas",
                      "Converse": "Texas",
                      "Griffin": "Georgia",
                      "Shreveport": "Louisiana",
                      "Cheshire": "Connecticut",
                      "Sayreville": "New Jersey",
                      "El Reno": "Oklahoma",
                      "Baldwin": "New York",
                      "Maumelle": "Arkansas",
                      "North Tustin": "California",
                      "Grapevine": "Texas",
                      "Wenatchee": "Washington",
                      "Saint Petersburg": "Florida",
                      "Oro Valley": "Arizona",
                      "Hibbing": "Minnesota",
                      "Crystal Lake": "Illinois",
                      "Apex": "North Carolina",
                      "Glenvar Heights": "Florida",
                      "Turlock": "California",
                      "Princeton": "Florida",
                      "Deerfield": "Illinois",
                      "Modesto": "California",
                      "Massapequa": "New York",
                      "Bay Shore": "New York",
                      "Gilroy": "California",
                      "Sun City Center": "Florida",
                      "Freeport": "New York",
                      "Barberton": "Ohio",
                      "Creve Coeur": "Missouri",
                      "Norwalk": "California",
                      "Portland": "Oregon",
                      "Elizabeth City": "North Carolina",
                      "West Puente Valley": "California",
                      "Tonawanda": "New York",
                      "San Jacinto": "California",
                      "Quincy": "Massachusetts",
                      "Kailua": "Hawaii",
                      "Spokane": "Washington",
                      "Oak Forest": "Illinois",
                      "Torrance": "California",
                      "Overland Park": "Kansas",
                      "Security-Widefield": "Colorado",
                      "Starkville": "Mississippi",
                      "Ives Estates": "Florida",
                      "Pensacola": "Florida",
                      "Schofield Barracks": "Hawaii",
                      "Lenoir": "North Carolina",
                      "New Orleans": "Louisiana",
                      "Kennesaw": "Georgia",
                      "Rosedale": "Maryland",
                      "Safety Harbor": "Florida",
                      "Lowell": "Massachusetts",
                      "Yucaipa": "California",
                      "Mitchell": "South Dakota",
                      "Cleburne": "Texas",
                      "Kansas City": "Kansas",
                      "DeKalb": "Illinois",
                      "Tamiami": "Florida",
                      "Chicago Heights": "Illinois",
                      "Granger": "Indiana",
                      "Marysville": "Washington",
                      "Tukwila": "Washington",
                      "Wyckoff": "New Jersey",
                      "Boardman": "Ohio",
                      "Trotwood": "Ohio",
                      "Chatsworth": "California",
                      "Wilmette": "Illinois",
                      "Michigan City": "Indiana",
                      "Hickory": "North Carolina",
                      "Hammond": "Indiana",
                      "Hanover": "Massachusetts",
                      "Coral Terrace": "Florida",
                      "Downers Grove": "Illinois",
                      "North Miami Beach": "Florida",
                      "Winter Park": "Florida",
                      "Garfield Heights": "Ohio",
                      "Poughkeepsie": "New York",
                      "Des Moines": "Iowa",
                      "Fort Smith": "Arkansas",
                      "White Bear Lake": "Minnesota",
                      "Somerville": "Massachusetts",
                      "Santa Monica": "California",
                      "Coral Springs": "Florida",
                      "Faribault": "Minnesota",
                      "Hawthorne": "California",
                      "Sanford": "Florida",
                      "Concord": "Missouri",
                      "Mount Laurel": "New Jersey",
                      "Lake Shore": "Maryland",
                      "Lackawanna": "New York",
                      "Saint Louis Park": "Minnesota",
                      "Northport": "Alabama",
                      "Westchester": "Florida",
                      "Indianapolis": "Indiana",
                      "Gardena": "California",
                      "Country Club Hills": "Illinois",
                      "Pendleton": "Oregon",
                      "Peachtree City": "Georgia",
                      "Landover": "Maryland",
                      "Paso Robles": "California",
                      "Hyattsville": "Maryland",
                      "Port Orange": "Florida",
                      "Bethlehem": "Pennsylvania",
                      "Hermosa Beach": "California",
                      "Indio": "California",
                      "Riverbank": "California",
                      "Sacramento": "California",
                      "Wauwatosa": "Wisconsin",
                      "Conyers": "Georgia",
                      "Merced": "California",
                      "Allendale": "Michigan",
                      "Elmwood Park": "Illinois",
                      "Tarpon Springs": "Florida",
                      "Hialeah": "Florida",
                      "Richfield": "Minnesota",
                      "Morristown": "New Jersey",
                      "Penn Hills": "Pennsylvania",
                      "Winona": "Minnesota",
                      "Woodmere": "New York",
                      "Rutherford": "New Jersey",
                      "Kannapolis": "North Carolina",
                      "Bridgeport": "Connecticut",
                      "Whitehall": "Ohio",
                      "Ruskin": "Florida",
                      "Arnold": "Missouri",
                      "Oakland": "California",
                      "Leawood": "Kansas",
                      "Odenton": "Maryland",
                      "Conroe": "Texas",
                      "Mira Loma": "California",
                      "Braintree": "Massachusetts",
                      "Hurst": "Texas",
                      "Lubbock": "Texas",
                      "York": "Pennsylvania",
                      "Bergenfield": "New Jersey",
                      "Bethel Park": "Pennsylvania",
                      "Normal": "Illinois",
                      "Burnsville": "Minnesota",
                      "Gilbert": "Arizona",
                      "Mount Prospect": "Illinois",
                      "San Clemente": "California",
                      "Taylorsville": "Utah",
                      "Kenner": "Louisiana",
                      "Draper": "Utah",
                      "Elizabethtown": "Kentucky",
                      "Lansing": "Michigan",
                      "Woburn": "Massachusetts",
                      "Weymouth": "Massachusetts",
                      "Bismarck": "North Dakota",
                      "Avon Lake": "Ohio",
                      "South River": "New Jersey",
                      "Berea": "Ohio",
                      "Marina": "California",
                      "Buffalo": "Minnesota",
                      "College Park": "Maryland",
                      "Sylvania": "Ohio",
                      "Milpitas": "California",
                      "Reno": "Nevada",
                      "Seattle": "Washington",
                      "Jasmine Estates": "Florida",
                      "Florida Ridge": "Florida",
                      "Cibolo": "Texas",
                      "Sulphur": "Louisiana",
                      "East Ridge": "Tennessee",
                      "Eagle Mountain": "Utah",
                      "Spanaway": "Washington",
                      "El Centro": "California",
                      "Norco": "California",
                      "Wekiwa Springs": "Florida",
                      "Barrington": "Rhode Island",
                      "Cerritos": "California",
                      "Vineland": "New Jersey",
                      "Mokena": "Illinois",
                      "Belvedere Park": "Georgia",
                      "Niagara Falls": "New York",
                      "Green Valley": "Arizona",
                      "Scotch Plains": "New Jersey",
                      "Woodstock": "Illinois",
                      "Hillcrest Heights": "Maryland",
                      "Lorain": "Ohio",
                      "Dracut": "Massachusetts",
                      "Goodyear": "Arizona",
                      "Wilkinsburg": "Pennsylvania",
                      "Brookline": "Massachusetts",
                      "Albany": "New York",
                      "Madisonville": "Kentucky",
                      "Carney": "Maryland",
                      "Aiken": "South Carolina",
                      "Sedalia": "Missouri",
                      "Bend": "Oregon",
                      "Temecula": "California",
                      "Islip": "New York",
                      "Wichita": "Kansas",
                      "Cooper City": "Florida",
                      "Fort Thomas": "Kentucky",
                      "Stow": "Ohio",
                      "Millville": "New Jersey",
                      "Casper": "Wyoming",
                      "Camarillo": "California",
                      "Loma Linda": "California",
                      "Highland Village": "Texas",
                      "Miami": "Florida",
                      "Avenel": "New Jersey",
                      "Deltona": "Florida",
                      "Margate": "Florida",
                      "Sarasota": "Florida",
                      "Derry": "New Hampshire",
                      "Echo Park": "California",
                      "The Bronx": "New York",
                      "Cortland": "New York",
                      "Elyria": "Ohio",
                      "The Hammocks": "Florida",
                      "Norman": "Oklahoma",
                      "Cumberland": "Maryland",
                      "La Crescenta-Montrose": "California",
                      "Chelsea": "Massachusetts",
                      "Peabody": "Massachusetts",
                      "Mesquite": "Nevada",
                      "Macomb": "Illinois",
                      "Rowland Heights": "California",
                      "Marquette": "Michigan",
                      "Belle Glade": "Florida",
                      "North Potomac": "Maryland",
                      "West Islip": "New York",
                      "Rome": "Georgia",
                      "Alexandria": "Louisiana",
                      "Spanish Fork": "Utah",
                      "Fern Creek": "Kentucky",
                      "Montgomery Village": "Maryland",
                      "San Tan Valley": "Arizona",
                      "Panama City": "Florida",
                      "Cloverly": "Maryland",
                      "Los Altos": "California",
                      "South San Jose Hills": "California",
                      "Fairhope": "Alabama",
                      "Allen": "Texas",
                      "West Mifflin": "Pennsylvania",
                      "Havelock": "North Carolina",
                      "Oxford": "Mississippi",
                      "Provo": "Utah",
                      "Alum Rock": "California",
                      "Frisco": "Texas",
                      "San Gabriel": "California",
                      "Pleasant Grove": "Utah",
                      "South Jordan": "Utah",
                      "Yuba City": "California",
                      "Rye": "New York",
                      "Lee's Summit": "Missouri",
                      "Murrieta": "California",
                      "Round Lake Beach": "Illinois",
                      "Newport Beach": "California",
                      "Rosemount": "Minnesota",
                      "Stoughton": "Massachusetts",
                      "Pueblo West": "Colorado",
                      "Edgewood": "Maryland",
                      "Gautier": "Mississippi",
                      "Brenham": "Texas",
                      "Dumont": "New Jersey",
                      "Fort Worth": "Texas",
                      "Tillmans Corner": "Alabama",
                      "Collinsville": "Illinois",
                      "Port Charlotte": "Florida",
                      "Westmont": "California",
                      "Dover": "Delaware",
                      "Long Branch": "New Jersey",
                      "DeLand": "Florida",
                      "Moline": "Illinois",
                      "Rossville": "Maryland",
                      "West Linn": "Oregon",
                      "Brentwood Estates": "Tennessee",
                      "Minnetonka": "Minnesota",
                      "Hanahan": "South Carolina",
                      "Makakilo City": "Hawaii",
                      "Pikesville": "Maryland",
                      "Dubuque": "Iowa",
                      "Tupelo": "Mississippi",
                      "West Seneca": "New York",
                      "Parkville": "Maryland",
                      "Marlborough": "Massachusetts",
                      "Long Island City": "New York",
                      "Mobile": "Alabama",
                      "Lake Zurich": "Illinois",
                      "Fort Lee": "New Jersey",
                      "Merrillville": "Indiana",
                      "Mason": "Ohio",
                      "Hilo": "Hawaii",
                      "Goshen": "Indiana",
                      "Valdosta": "Georgia",
                      "Kingman": "Arizona",
                      "Dyer": "Indiana",
                      "Cedar City": "Utah",
                      "Tanque Verde": "Arizona",
                      "Covina": "California",
                      "North Canton": "Ohio",
                      "Saint Andrews": "South Carolina",
                      "Washington": "Illinois",
                      "Johnston": "Iowa",
                      "Yonkers": "New York",
                      "Perris": "California",
                      "Apple Valley": "Minnesota",
                      "Southgate": "Michigan",
                      "Hilliard": "Ohio",
                      "Foothill Farms": "California",
                      "Deer Park": "New York",
                      "Elmira": "New York",
                      "Fairhaven": "Massachusetts",
                      "South Old Bridge": "New Jersey",
                      "Ewa Gentry": "Hawaii",
                      "Fort Washington": "Maryland",
                      "Solon": "Ohio",
                      "Williamstown": "New Jersey",
                      "Corcoran": "California",
                      "Sioux Falls": "South Dakota",
                      "Elk River": "Minnesota",
                      "Mauldin": "South Carolina",
                      "Beltsville": "Maryland",
                      "McKinleyville": "California",
                      "Bell": "California",
                      "Derry Village": "New Hampshire",
                      "Pittsfield": "Massachusetts",
                      "Humble": "Texas",
                      "Andover": "Minnesota",
                      "Duarte": "California",
                      "Missoula": "Montana",
                      "Stockbridge": "Georgia",
                      "Port Huron": "Michigan",
                      "Spartanburg": "South Carolina",
                      "Bayonet Point": "Florida",
                      "East Concord": "New Hampshire",
                      "Lealman": "Florida",
                      "Warner Robins": "Georgia",
                      "Doral": "Florida",
                      "Ocoee": "Florida",
                      "Cuyahoga Falls": "Ohio",
                      "Oak Creek": "Wisconsin",
                      "Ballenger Creek": "Maryland",
                      "North Port": "Florida",
                      "Idaho Falls": "Idaho",
                      "Wilmington": "North Carolina",
                      "Nixa": "Missouri",
                      "Inglewood": "California",
                      "Kenmore": "Washington",
                      "San Diego": "California",
                      "Elizabeth": "New Jersey",
                      "Baytown": "Texas",
                      "Granite Bay": "California",
                      "Canyon Lake": "Texas",
                      "Blytheville": "Arkansas",
                      "Oakley": "California",
                      "Boca Raton": "Florida",
                      "Shaker Heights": "Ohio",
                      "Fairfield": "Ohio",
                      "Kalamazoo": "Michigan",
                      "Leisure City": "Florida",
                      "Moscow": "Idaho",
                      "Charleston": "South Carolina",
                      "Kings Park": "New York",
                      "Kearns": "Utah",
                      "Cambridge": "Massachusetts",
                      "Laurinburg": "North Carolina",
                      "East Northport": "New York",
                      "Ken Caryl": "Colorado",
                      "Chapel Hill": "North Carolina",
                      "Hialeah Gardens": "Florida",
                      "Rosamond": "California",
                      "Tucker": "Georgia",
                      "Sun City": "Arizona",
                      "South El Monte": "California",
                      "Amherst": "New York",
                      "Desert Hot Springs": "California",
                      "Ronkonkoma": "New York",
                      "Lyndhurst": "New Jersey",
                      "Siloam Springs": "Arkansas",
                      "Watertown": "Massachusetts",
                      "Middleburg Heights": "Ohio",
                      "Bell Gardens": "California",
                      "Hot Springs": "Arkansas",
                      "West Memphis": "Arkansas",
                      "West Scarborough": "Maine",
                      "Holyoke": "Massachusetts",
                      "Fairwood": "Washington",
                      "Pittsburg": "Kansas",
                      "Seabrook": "Maryland",
                      "Youngstown": "Ohio",
                      "Redan": "Georgia",
                      "Atwater": "California",
                      "Anaheim": "California",
                      "Bostonia": "California",
                      "Palm Harbor": "Florida",
                      "Prescott": "Arizona",
                      "East Providence": "Rhode Island",
                      "Edmond": "Oklahoma",
                      "Ocean Acres": "New Jersey",
                      "East Florence": "Alabama",
                      "Hayward": "California",
                      "Needham": "Massachusetts",
                      "Dearborn": "Michigan",
                      "Ramsey": "Minnesota",
                      "Johns Creek": "Georgia",
                      "Wallingford Center": "Connecticut",
                      "Coram": "New York",
                      "West Coon Rapids": "Minnesota",
                      "Bakersfield": "California",
                      "Winston-Salem": "North Carolina",
                      "Slidell": "Louisiana",
                      "Riverton": "Utah",
                      "Ossining": "New York",
                      "Cookeville": "Tennessee",
                      "Tewksbury": "Massachusetts",
                      "Port Chester": "New York",
                      "Rolla": "Missouri",
                      "Rock Hill": "South Carolina",
                      "Graham": "Washington",
                      "East Brunswick": "New Jersey",
                      "Greenville": "Texas",
                      "Fort Collins": "Colorado",
                      "Suwanee": "Georgia",
                      "New City": "New York",
                      "Duncan": "Oklahoma",
                      "Forest Park": "Georgia",
                      "Daphne": "Alabama",
                      "Mountlake Terrace": "Washington",
                      "Memphis": "Tennessee",
                      "The Villages": "Florida",
                      "Nipomo": "California",
                      "Temple City": "California",
                      "Alhambra": "California",
                      "Northfield": "Minnesota",
                      "Bountiful": "Utah",
                      "Tooele": "Utah",
                      "Santa Fe Springs": "California",
                      "University": "Florida",
                      "Fresno": "Texas",
                      "Buckeye": "Arizona",
                      "Allen Park": "Michigan",
                      "Mount Lebanon": "Pennsylvania",
                      "Brook Park": "Ohio",
                      "North Plainfield": "New Jersey",
                      "Hoover": "Alabama",
                      "Benicia": "California",
                      "Hunt Valley": "Maryland",
                      "Sumter": "South Carolina",
                      "Mandan": "North Dakota",
                      "Biddeford": "Maine",
                      "Cartersville": "Georgia",
                      "Bowie": "Maryland",
                      "Yukon": "Oklahoma",
                      "Anacortes": "Washington",
                      "Morton": "Illinois",
                      "Universal City": "California",
                      "Hercules": "California",
                      "Towson": "Maryland",
                      "Sioux City": "Iowa",
                      "Brunswick": "Georgia",
                      "West Hempstead": "New York",
                      "Auburn Hills": "Michigan",
                      "Aspen Hill": "Maryland",
                      "West Hartford": "Connecticut",
                      "Houma": "Louisiana",
                      "Jeffersonville": "Indiana",
                      "Saratoga": "California",
                      "Delano": "California",
                      "Sunny Isles Beach": "Florida",
                      "Saint Peters": "Missouri",
                      "Oak Ridge": "Tennessee",
                      "Leesburg": "Florida",
                      "Florissant": "Missouri",
                      "Hicksville": "New York",
                      "Federal Way": "Washington",
                      "Joplin": "Missouri",
                      "Weston": "Florida",
                      "Davenport": "Iowa",
                      "Abington": "Massachusetts",
                      "Novato": "California",
                      "Laplace": "Louisiana",
                      "Portsmouth": "New Hampshire",
                      "Eden Prairie": "Minnesota",
                      "Mableton": "Georgia",
                      "Sunrise Manor": "Nevada",
                      "Campbell": "California",
                      "Waukegan": "Illinois",
                      "Poplar Bluff": "Missouri",
                      "Midland": "Texas",
                      "Pascagoula": "Mississippi",
                      "Ottumwa": "Iowa",
                      "Walker": "Michigan",
                      "Danville": "Illinois",
                      "West Carson": "California",
                      "Hereford": "Texas",
                      "Wilton": "Connecticut",
                      "San Bernardino": "California",
                      "Encinitas": "California",
                      "Los Gatos": "California",
                      "Sheridan": "Wyoming",
                      "Burbank": "Illinois",
                      "Riverdale": "Georgia",
                      "Savage": "Minnesota",
                      "Galt": "California",
                      "Marana": "Arizona",
                      "Palos Hills": "Illinois",
                      "Thornton": "Colorado",
                      "Hermitage": "Pennsylvania",
                      "McHenry": "Illinois",
                      "Keene": "New Hampshire",
                      "Estero": "Florida",
                      "Cleveland": "Ohio",
                      "West Lake Sammamish": "Washington",
                      "Royal Oak": "Michigan",
                      "Superior": "Wisconsin",
                      "Lynn Haven": "Florida",
                      "Green Bay": "Wisconsin",
                      "Makakilo": "Hawaii",
                      "Denton": "Texas",
                      "Euclid": "Ohio",
                      "Eagan": "Minnesota",
                      "Northglenn": "Colorado",
                      "Duncanville": "Texas",
                      "Bethany": "Oklahoma",
                      "Oceanside": "New York",
                      "Pocatello": "Idaho",
                      "Cicero": "Illinois",
                      "Keizer": "Oregon",
                      "El Cerrito": "California",
                      "New Lenox": "Illinois",
                      "Bozeman": "Montana",
                      "Beverly": "Massachusetts",
                      "Niles": "Ohio",
                      "Streamwood": "Illinois",
                      "Kirkland": "Washington",
                      "West Allis": "Wisconsin",
                      "Springboro": "Ohio",
                      "North Druid Hills": "Georgia",
                      "Durant": "Oklahoma"}